# Setup

## Import

In [ ]:
import cgtools as cg
import collections
from cycler import cycler
import copy
import glob
import gromacstools as gt
from gromacstools.general import WorkingDir, run_bash
import itertools
import json
import matplotlib.pyplot as plt
import matplotlib as mpl
import numpy as np
from numpy.polynomial import Polynomial
import os
import re
import shutil
import scipy.constants as const
import scipy.optimize as optimize
import subprocess
import sys
import tempfile
import xml.etree.ElementTree as ET
import importlib

In [ ]:
sys.path.append('/home/marvin/research/code/votca/csg/share/scripts/inverse/')
import csg_functions as csg
import iie

In [ ]:
class oconst: pass
oconst.k_gro = const.k * const.N_A * 1e-3
oconst.h_gro = const.h * const.N_A * 1e-3 * 1e12
oconst.f_gro = 138.935458  # electric conversion factor: V = f q²/r
oconst.epsilon_0_gro = const.epsilon_0 * const.N_A * 1e3
oconst.rec_cm_per_THz = 1e12 / const.c / 100
oconst.bar_per_md_pressure = 10**28 * const.u

## often used helper functions

In [ ]:
def check_job_stati(jobids, remote_host):
    stati = gt.remote.check_slurm_jobs(jobids, remote_host)

    # print status for each job
    completed_jobids = []
    for jobid, status in zip(jobids, stati):
        print(jobid, status)
        if (status in ('FAILED', 'COMPLETED', None)
            or status.startswith('CANCELLED')):
            completed_jobids.append(jobid)

    # remove jobids which are completed
    new_jobids = [jobid for jobid in jobids if jobid not in completed_jobids]
    return new_jobids

In [ ]:
def gen_moltype_list(fg_topology, statepoint):
    """Generate moltype_list from fg_topology and statepoint."""
    moltype_list = [{'name': moltype_key, **moltype}
                    for moltype_key, moltype in fg_topology['moltypes'].items()
                    if statepoint['composition'][moltype_key] > 0]
    for moltype in moltype_list:
        moltype['atoms'] = moltype.pop('beads')
        moltype['atoms'] = [{'name': atom_key,
                             'mass': fg_topology['beadtypes'][atom['type']]['mass'],
                             **atom}
                            for atom_key, atom in moltype['atoms'].items()]
        moltype['nmols'] = statepoint['composition'][moltype['name']]
    return moltype_list

In [ ]:
def compare_dict_tree(dict1, dict2):
    if json.dumps(dict1, sort_keys=True) == json.dumps(dict2, sort_keys=True):
        return True
    else:
        return False

In [ ]:
def replace_dict_tree(sub_dict, sub_repl_dict, create_non_existing=True):
    for k, v in sub_repl_dict.items():
        if not create_non_existing:
            if k not in sub_dict.keys():
                continue
        if isinstance(v, dict) and k in sub_dict.keys():
            sub_dict[k] = replace_dict_tree(sub_dict[k], sub_repl_dict[k], create_non_existing)
        else:
            sub_dict[k] = sub_repl_dict[k]
    return sub_dict

In [ ]:
def test_replace_dict_tree():
    orig = {'a': {'b': {'c1': 1, 'c2': 2}}, 'x': {'y': 100, 'z': 100}}
    repl = {'a': {'b': {'c2': 3}}, 'x': {'z': 200}, 'foo': 'bar'}
    print(replace_dict_tree(orig, repl))

test_replace_dict_tree()

In [ ]:
def apply_and_replace_string_function_tuples(sub_dict, values_dict):
    """Go through a dict structure recursively replacing (string, functin) tuples."""
    for k, v in sub_dict.items():
        if isinstance(v, tuple) and len(v) == 2 and isinstance(v[0], str) and callable(v[1]) and v[0] in values_dict.keys():
            sub_dict[k] = v[1](values_dict[v[0]])  # call functions
            if isinstance(sub_dict[k], dict) or (isinstance(sub_dict[k], tuple) and len(sub_dict[k]) == 2 and isinstance(sub_dict[k][0], str) and callable(sub_dict[k][1])):
                sub_dict[k] = apply_and_replace_string_function_tuples(sub_dict[k], values_dict)  # go through resulting dict, too
        elif isinstance(v, dict):
            sub_dict[k] = apply_and_replace_string_function_tuples(sub_dict[k], values_dict)
    return sub_dict

In [ ]:
def test_apply_and_replace_string_function_tuples():
    #orig = {'a': {'b': {'c1': 1, 'c2': ('c', lambda x: 2*x)}}, 'x': {'y': 100, 'z': 100}}
    orig = {'a': {'b': {'c1': 1, 'c2': ('c', lambda c: c)}}, 'x': {'y': 100, 'z': 100, 'g': ('e', lambda e: e)}}
    #values_dict = {'c': 3}
    values_dict = {'c': {'foo': ('e', lambda e: e+1)}, 'e': 200}
    print(apply_and_replace_string_function_tuples(orig, values_dict))

test_apply_and_replace_string_function_tuples()

In [ ]:
def get_values_in_dict_tree(dict_tree, path):
    """Generate values in dict_tree that match path with None as wildcard"""
    if len(path) == 0:  # found element
        yield dict_tree
    else:
        if path[0] is None:
            for value in dict_tree.values():
                yield from get_values_in_dict_tree(value, path[1:])
        elif path[0] in dict_tree.keys():
            yield from get_values_in_dict_tree(dict_tree[path[0]], path[1:])

In [ ]:
def change_dict_tree_with_path(dict_tree, path, value, create_non_existing=True):
    # path elements can be lists to do multiple children
    if isinstance(path[0], list):
        all_path0 = path[0]
    else:
        all_path0 = [path[0]]
    for path0 in all_path0:
        # create something new
        if path0 not in dict_tree.keys() and create_non_existing:
            if len(path) == 1:  # found element
                # new end node
                dict_tree[path0] = value
            else:
                # create new child node
                dict_tree[path0] = {}
                change_dict_tree_with_path(dict_tree[path0], path[1:], value, create_non_existing=create_non_existing)
        # only substitute what is there
        elif path0 in dict_tree.keys():
            if len(path) == 1:  # found element
                # substitute by value
                dict_tree[path0] = value
            else:
                # substitue in sub-tree
                change_dict_tree_with_path(dict_tree[path0], path[1:], value, create_non_existing=create_non_existing)

In [ ]:
def readin_table(filename):
    data = np.loadtxt(filename, dtype=str, comments=['#', '@'])
    x = data[:, 0].astype(float)
    y = data[:, 1].astype(float)
    try:
        y_flag = data[:, 2].astype('S1')
    except:
        y_flag = [''] * len(x)
    return x, y, y_flag

In [ ]:
def writeout_table(filename, x, y, flag):
    data = np.vstack((
        np.array(x, dtype=np.object_),
        np.array(y, dtype=np.object_),
        np.array(flag, dtype=np.object_),
    )).T
    np.savetxt(filename, data, fmt=['%.4f', '%.8e', '%s'])

In [ ]:
# test writeout
writeout_table('/tmp/foo.xvg', [1, 2], [2, 4], ['o', 'i'])
!cat /tmp/foo.xvg

In [ ]:
def readin_table_gromacs(filename, U_col=7, F_col=8):
    data = np.loadtxt(filename, dtype=str, comments=['#', '@'])
    x = data[:, 0].astype(float)
    U = data[:, U_col].astype(float)
    F = data[:, F_col].astype(float)
    return x, U, F

In [ ]:
def uniquify(seq):
    seen = set()
    seen_add = seen.add
    return [x for x in seq if not (x in seen or seen_add(x))]

In [ ]:
def gen_statepoints(state):
    # prepare statepoints
    if state['type'] == 'single':
        statepoints = [{'path': '.', **state}]
    elif state['type'] == 'multi':
        #statepoints = copy.deepcopy(cg_problem['state'])
        statepoints = []
        for i in range(len(state['names'])):
            statepoint = {key: value[i] for key, value in state.items() if key not in ('tags', 'type', 'composition', 'votca-settings')}
            statepoint['composition'] = {key: value[i] for key, value in state['composition'].items()}
            statepoint['path'] = statepoint['names']
            del statepoint['names']
            statepoint['type'] = "multi-sub"
            statepoints.append(statepoint)
    return statepoints

## Remote computing resource

In [ ]:
def gen_remote_stuff(remote_host, remote_partition, ntasks, votca=False, **kwargs):
    remote_dir_base = os.path.join("/home/mbernhardt/run/projects/iie/solvents")

    fg_gromacs_module = {
        'batch': 'gromacs /6zq3ypk',   # gromacs@2021.5~blas+cuda
        'batchgpu': 'gromacs /6zq3ypk',    # gromacs@2021.5~blas+cuda
        'milan': 'gromacs /furgxnd',    # gromacs@2021.5~blas+cuda
        'rtx3080': 'gromacs /furgxnd',    # gromacs@2021.5~blas+cuda
    }[remote_partition]
    votca_gromacs_module = {
        'batch': 'gromacs /ze62fhc',    # gromacs@2019.6~blas+cuda
        'batchgpu': 'gromacs /ze62fhc',    # gromacs@2019.6~blas+cuda
        'milan': 'gromacs /aeshyvv',    # gromacs@2019.6~blas+cuda
        'rtx3080': 'gromacs /aeshyvv',    # gromacs@2019.6~blas+cuda
    }[remote_partition]
    sbatch_arguments = [
        '--job-name=cg',
        f'--partition={remote_partition}',
        f"--ntasks={ntasks}",
        '--time=24:00:00',
    ]
    for key, arg in kwargs.items():
        if arg is not None:
            sbatch_arguments.append(f"--{key.replace('_', '-')}={arg}")
    sbatch_arguments_section = '\n'.join((f'#SBATCH {arg}' for arg in sbatch_arguments))
    votca_version = "votca-milan" if remote_partition in ['milan', 'rtx3080'] else "votca"
    remote_header = f"""#!/bin/sh
{sbatch_arguments_section}

set -eo pipefail  # -u does not work with VOTCA and/or conda?

# Create local directory
JOBTMP="/tmp/$(mktemp -u data${{SLURM_JOB_ID}}XXXXXXXXXXXXXX)"
mkdir $JOBTMP

# enable spack
export SPACK_PYTHON=/usr/bin/python3.6
export SPACK_ROOT=/shared/spack
. $SPACK_ROOT/share/spack/setup-env.sh

# load modules
module purge
spack unload --all
spack_gmx_for_fg="{fg_gromacs_module}"  # libraries for MD, load before calling votca
spack_gmx_for_votca="{votca_gromacs_module}"  # libraries for Votca, load before calling votca
spack load $spack_gmx_for_fg
"""
    if votca:
        remote_header += f"""
spack load /m67paft  # boost@1.78.0
spack load /b5wq7vk  # gsl@2.7~external-cblas
spack load /h5unuli  # fftw@3.3.10+mpi~openmp~pfft_patches precision=double,float

source ~/software/miniconda3/etc/profile.d/conda.sh
conda activate
source /home/mbernhardt/software/{votca_version}/bin/VOTCARC.bash
"""
    remote_footer = """
# Remove local directory
rm -rf $JOBTMP
"""
    return remote_dir_base, remote_header, remote_footer, {'remote_host': remote_host, 'remote_partion': remote_partition, 'ntasks': ntasks, 'votca': votca, **kwargs}

remote_host = 'sniffa'
def test():
    remote_dir_base, remote_header, remote_footer, remote_args = gen_remote_stuff(remote_host, 'rtx3080', ntasks=48, gres='gpu:1', votca=True)
    print(remote_header)
test()

In [ ]:
if 'jobids' not in locals():
    jobids = []

## Coarse-graining setup

### miscellaneous

In [ ]:
# this could ideally be calculated from the box size and the cut-off
# or mdrun can do it itself?
max_cores_mdrun_systype = {'neon-argon': 8, 'ethanol-water': 18, 'water-spc': 48, 'naphtalene': 18, 'nacl-water': 48, 'methanol': 18, 'methanol-water': 48, 'methane': 27}
combination_rule = {
    'oplsaa.ff': lambda sig1, sig2, eps1, eps2: ((sig1*sig2)**(1/2), (eps1*eps2)**(1/2)),  # geometric
    'ligpargen': lambda sig1, sig2, eps1, eps2: ((sig1*sig2)**(1/2), (eps1*eps2)**(1/2)),  # geometric
    'madrid': lambda sig1, sig2, eps1, eps2: ((sig1+sig2)/2, (eps1*eps2)**(1/2)),  # Lorentz-Berthelot
}

### molecules 

In [ ]:
from molecules import molecules
molecules.keys()

### fg_sys_types

In [ ]:
def gen_fg_sys_types():
    fg_sys_types = {}
    for molecule_name, molecule_data in molecules.items():
        beadtypes, beads = gt.itp.get_atomtypes_atoms(f"ligpargen/{molecule_name}_mod.itp")
        fg_sys_types[molecule_name] = {
            'tags': [],
            'md-settings': {
                'md-program': 'gromacs',
                'dt': 0.0005,
                'tau-t': 1,
                'tau-p': 10,
                'integrator+thermostat': 'md+v-rescale',
            },
            'topology': {
                'ff-key': 'ligpargen',
                'beadtypes': beadtypes,
                'moltypes': {
                    molecule_name: {
                        'itp': f'{molecule_name}.itp',
                        'short-name': molecule_data['short-name'],
                        'beads': beads,
                    }
                }
            },
            'meta': {'type': 'pure', 'molecules': [molecule_name]},
        }
    # mixtures
    for (m1_name, m1_data), (m2_name, m2_data) in itertools.product(molecules.items(), molecules.items()):
        if m1_name >= m2_name:  # this effectively sorts the molecule combinations
            continue
        m1_file_name = m1_name.replace(' ', '_')
        m2_file_name = m2_name.replace(' ', '_')
        m1_beadtypes, m1_beads = gt.itp.get_atomtypes_atoms(f"ligpargen/{m1_file_name}_mod.itp")
        m2_beadtypes, m2_beads = gt.itp.get_atomtypes_atoms(f"ligpargen/{m2_file_name}_mod.itp")
        fg_sys_types[f"mix-{m1_name}+{m2_name}"] = {
            'tags': [],
            'md-settings': {
                'md-program': 'gromacs',
                'dt': 0.0005,
                'tau-t': 1,
                'tau-p': 10,
                'integrator+thermostat': 'md+v-rescale',
            },
            'topology': {
                'ff-key': 'ligpargen',
                'beadtypes': m1_beadtypes | m2_beadtypes,
                'moltypes': {
                    m1_name: {
                        'itp': f'{m1_file_name}.itp',
                        'short-name': m1_data['short-name'],
                        'beads': m1_beads,
                    },
                    m2_name: {
                        'itp': f'{m2_file_name}.itp',
                        'short-name': m2_data['short-name'],
                        'beads': m2_beads,
                    }
                }
            },
            'meta': {'type': 'mix', 'molecules': [m1_name, m2_name]},
        }
        
    return fg_sys_types
        
fg_sys_types = gen_fg_sys_types()
fg_sys_types['mix-acetone+ethanol']

### states

In [ ]:
def gen_states():
    states = {
        'pure': {},
        #'pure-large': {},
        'xrange2': {},
        'x0.5': {},
    }
    for fg_sys_type_key, fg_sys_type in fg_sys_types.items():
        if fg_sys_type['meta']['type'] == 'pure':
            states['pure'][fg_sys_type_key] = {
                'tags': [],
                'type': 'single',
                'composition': {
                    key: 3000 for key in fg_sys_type['topology']['moltypes'].keys()
                },
                'temperature': 293.15,
                'pressure-fg': 1,
                'volume-cg': 'fg average',
                'votca-settings': {'inverse': {
                    'gauss_newton': {'pressure_constraint': 1},
                    'cleanlist': "../jobtmp/traj.xtc",
                    'gromacs': {'traj': "../jobtmp/traj.xtc"},
                }},
            }
            #states['pure-large'][fg_sys_type_key] = {
                #'tags': [],
                #'type': 'single',
                #'composition': {
                    #key: 10000 for key in fg_sys_type['topology']['moltypes'].keys()
                #},
                #'temperature': 293.15,
                #'pressure-fg': 1,
                #'volume-cg': 'fg average',
                #'votca-settings': {'inverse': {
                    #'gauss_newton': {'pressure_constraint': 1},
                    #'cleanlist': "../jobtmp/traj.xtc",
                    #'gromacs': {'traj': "../jobtmp/traj.xtc"},
                #}},
            #}
        elif fg_sys_type['meta']['type'] == 'mix':
            states['xrange2'][fg_sys_type_key] = {
                'tags': [],
                'type': 'multi',
                'names': ['x0.25', 'x0.75'],
                'weights': [0.5, 0.5],
                'composition': {
                    key: [[750, 2250], [2250, 750]][k] for k, key in enumerate(fg_sys_type['topology']['moltypes'].keys())
                },
                'temperature': [293.15]*2,
                'pressure-fg': [1]*2,
                'volume-cg': ['fg average']*2,
                'votca-settings': {'inverse': {
                    #'iie': {'pressure_constraint': 1},
                    'cleanlist': "../../jobtmp/traj-$state.xtc",
                    'gromacs': {'traj': "../../jobtmp/traj-$state.xtc"},
                }},
            }
            states['x0.5'][fg_sys_type_key] = {
                'tags': [],
                'type': 'single',
                'composition': {
                    key: 1500 for key in fg_sys_type['topology']['moltypes'].keys()
                },
                'temperature': 293.15,
                'pressure-fg': 1,
                'volume-cg': 'fg average',
                'votca-settings': {'inverse': {
                    'gauss_newton': {'pressure_constraint': 1},
                    'cleanlist': "../jobtmp/traj.xtc",
                    'gromacs': {'traj': "../jobtmp/traj.xtc"},
                }},
            }
    return states
states = gen_states()
#states['pure']['acetone']
#states['xrange2']['mix-acetone+ethanol']
states['x0.5']['mix-acetone+ethanol']

### mappings

In [ ]:
mappings = {
    '1bead': {
        'tags': [],
        'pos-weighting': 'mass-unity',
        'charge-weighting': 'zero',
    },
}

### cg_sys_types

In [ ]:
# define either bonds -> the bond has to be definded by the type of the two beads (works not for A4 naphtalene)
# or define bondtypes -> the bondtypes can have arbitrary names

def gen_cg_sys_types():
    cg_sys_types = {}
    for fg_sys_type_key, fg_sys_type in fg_sys_types.items():
        cg_sys_types[(fg_sys_type_key, '1bead')] = {
            'tags': [],
            'md-settings': {
                'md-program': 'gromacs',
                'dt': 0.002,
                'tau-t': 0.5,
            },
            'topology': {
                'moltypes': {
                    mt_key: {
                        'short-name': mt['short-name'] + 'CG',
                        'bonds': frozenset({}),
                    }
                    for mt_key, mt in fg_sys_type['topology']['moltypes'].items()
                },
            },
            'votca-settings': {},
            'functional-votca-settings-input': {
                'cut': 1.2,
                'cut_gn_res': 1.6,
                'cut_max': 3.2,
                'md-program': 'gromacs',
            },
            
        }
    
    return cg_sys_types

cg_sys_types = gen_cg_sys_types()
cg_sys_types

In [ ]:
def gen_mapping_moltypes_dict():
    mapping_moltypes_dict = {}
    for fg_sys_type_key, fg_sys_type in fg_sys_types.items():
        mapping_moltypes_dict[(fg_sys_type_key, '1bead')] = {
            mt_key: {'AB'[m]: {'type': 'AB'[m], 'fg-beads': tuple(mt['beads'].keys())}}
            for m, (mt_key, mt) in enumerate(fg_sys_type['topology']['moltypes'].items())
        }
    return mapping_moltypes_dict

mapping_moltypes_dict = gen_mapping_moltypes_dict()
mapping_moltypes_dict

In [ ]:
def gen_mapping(fg_sys_type_key, mappings, mapping_key):
    """This function could also generate the mapping based on fg_sys_type.
    
    For now it uses a dictionary."""
    mapping = copy.deepcopy(mappings[mapping_key])
    mapping['moltypes'] = mapping_moltypes_dict[(fg_sys_type_key, mapping_key)]
    return mapping

### votca settings

In [ ]:
def gen_votca_settings():
    votca_settings = {
        'hncgnt-hncinit': {
            'tags': [],
            'meta': {
                'singlestate': True, 'multistate': False,
                'all-interactions': True, 'selected-interactions': False,
                'max_step0': ('cut_max', lambda x: x),
            },
            'non-bonded': {
                'min': 0.0,
                'max': ('cut_gn_res', lambda x: x),  # will be replaced later
                'step': 0.008,
                'inverse': {
                    'do_potential': "1",
                    'is_target_distribution': 'true',
                    'imc': {'group': 'all'},
                    #'post_update': "scale",
                    #'post_update_options': {'scale': 0.67},
                },
                'improve_dist_near_core': {
                    'target': 'true',
                    'new': 'true',
                    'fit_start_g': 0.0001,
                    'fit_end_g': 0.1,
                },
            },
            'inverse': {
                'method': 'iie',
                'iterations_max': 15,
                'program': 'gromacs',
                'filelist': 'conf.gro grompp.mdp index.ndx topol.top table.xvg topology.xml',
                'cleanlist': '../jobtmp/traj.xtc',
                'gromacs': {
                    'equi_time': 100,
                    'table_end': ('cut', lambda x: x + 1.2),
                    #'grompp': {'opts': '-maxwarn 1'},
                    'traj': None,  # set depending on state['type'] to ../jobtmp/traj.xtc or ../../jobtmp/traj-$state.xtc
                    'mdrun': {'opts': '-pin on'},
                },
                'topol_xml': 'topology.xml',
                'initial_guess': {
                    'method': 'ie',
                    'cut_off': ('cut', lambda x: x),
                    'ie': {
                        'closure': 'hnc',
                    }
                },
                'iie': {
                    'algorithm': 'gauss-newton',
                    'closure': 'hnc',
                    'use_target_dcdh': 'true',
                },
                'gauss_newton': {
                    'cut_off': ('cut', lambda x: x),
                    'cut_residual': ('cut_gn_res', lambda x: x),
                    'pressure_constraint': 'change_me',
                    'residual_weighting': r'r**2/(g_tgt+1e-30)'
                },
                'verbose': 'step0+1',
            },
        },
    }
    # above: p-HNCGN
    
    # t-HNCN
    votca_settings['hncnt-hncinit'] = copy.deepcopy(votca_settings['hncgnt-hncinit'])
    votca_settings['hncnt-hncinit']['meta']['max_step0'] = ('cut_max', lambda x: x)  # more than double of cut, good for slow converging c (pyridin, dioxane)
    votca_settings['hncnt-hncinit']['non-bonded']['max'] = ('cut', lambda x: x)
    votca_settings['hncnt-hncinit']['inverse']['iie']['algorithm'] = 'newton'
    votca_settings['hncnt-hncinit']['inverse']['newton'] = {'cut_off': ('cut', lambda x: x)}  #, 'flatten_at_cut_off': 'true'}
    del votca_settings['hncnt-hncinit']['inverse']['gauss_newton']
    
    # IMC
    """
    votca_settings['imc-hncinit'] = copy.deepcopy(votca_settings['hncgnt-hncinit'])
    votca_settings['imc-hncinit']['meta']['only-fg-sys-type'] = ['pyridine', '1,4-dioxane', 'tert-butanol', 'ethylene_glycol']
    votca_settings['imc-hncinit']['inverse']['method'] = 'imc'
    votca_settings['imc-hncinit']['inverse']['imc'] = {'algorithm': 'gauss-newton',
                                                       'improve_jacobian_onset': 'true',
                                                       'onset_thresholds': '0.001 0.1',
                                                      }
    votca_settings['imc-hncinit']['inverse']['gauss_newton'] = {'cut_off': ('cut', lambda x: x),
                                                                'cut_residual': ('cut', lambda x: x),  # imitating Newton
                                                               }
    del votca_settings['imc-hncinit']['inverse']['iie']
    
    # p-IMC
    votca_settings['imcgn-hncinit'] = copy.deepcopy(votca_settings['imc-hncinit'])
    votca_settings['imcgn-hncinit']['inverse']['gauss_newton'] = {'cut_off': ('cut', lambda x: x),
                                                                  'cut_residual': ('cut_gn_res', lambda x: x),
                                                                  'pressure_constraint': 'change_me',
                                                                  'residual_weighting': r'r**2/(g_tgt+1e-30)'
                                                                 }
    """
    
    """
    votca_settings['hncnt-hncinitshort'] = copy.deepcopy(votca_settings['hncnt-hncinit'])
    votca_settings['hncnt-hncinitshort']['meta']['max_step0'] = ('cut', lambda x: 2 * x)  # only double, to show effects
    votca_settings['hncnt-hncinitshort']['inverse']['iterations_max'] = 0  # only to show initial guess
    votca_settings['hncnt-hncinitlong'] = copy.deepcopy(votca_settings['hncnt-hncinit']) # temp for checking c
    votca_settings['hncnt-hncinitlong']['meta']['max_step0'] = ('cut_gn_res', lambda x: 2 * x)
    votca_settings['hncnt-hncinitlong']['inverse']['iterations_max'] = 0
    """
    
    # scaling update
    for alg in ['n', 'gn']:
        votca_settings[f'hnc{alg}t0.67-hncinit'] = copy.deepcopy(votca_settings[f'hnc{alg}t-hncinit'])
        votca_settings[f'hnc{alg}t0.67-hncinit']['non-bonded']['inverse']['post_update'] = 'scale'
        votca_settings[f'hnc{alg}t0.67-hncinit']['non-bonded']['inverse']['post_update_options'] = {'scale': 0.67}
        votca_settings[f'hnc{alg}t0.67-hncinit']['inverse']['iterations_max'] = 15
        #votca_settings[f'hnc{alg}t0.67-hncinit']['meta']['only-fg-sys-type'] = ['pyridine', '1,4-dioxane', 'tert-butanol', 'ethylene_glycol']
        
    # IBI init
    for alg in ['gnt', 'gnt0.67']:
        votca_settings[f'hnc{alg}-ibiinit'] = copy.deepcopy(votca_settings[f'hnc{alg}-hncinit'])
        votca_settings[f'hnc{alg}-ibiinit']['meta']['only-fg-sys-type'] = ['ethylene_glycol']
        votca_settings[f'hnc{alg}-ibiinit']['inverse']['initial_guess'] = {'method': 'table',
                                                                           'cut_off': ('cut', lambda x: x),
                                                                          } 
        
    # selective-IBI x 0.67 no constraint
    votca_settings['sibi0.67-hncinit'] = copy.deepcopy(votca_settings['hncgnt0.67-hncinit'])
    votca_settings['sibi0.67-hncinit']['meta']['only-fg-sys-type'] = [
        'mix-ethanol+pyridine',
        'mix-ethylene_glycol+tert-butanol',
        'mix-ethylene_glycol+pyridine',
        'mix-acetone+pyridine',
        'mix-acetone+diethyl_ether',
        'mix-diethyl_ether+ethylene_glycol',
        'mix-ethyl_acetate+pyridine',
    ]
    votca_settings['sibi0.67-hncinit']['meta']['all-interactions'] = False
    votca_settings['sibi0.67-hncinit']['meta']['selected-interactions'] = True
    votca_settings['sibi0.67-hncinit']['inverse']['method'] = 'ibi'
    votca_settings['sibi0.67-hncinit']['non-bonded']['max'] = ('cut', lambda x: x)
    del votca_settings['sibi0.67-hncinit']['inverse']['iie']
    del votca_settings['sibi0.67-hncinit']['inverse']['gauss_newton']
    
    # selective-t-HNCGN x 0.67 no constraint
    votca_settings['shncgnt0.67-hncinit'] = copy.deepcopy(votca_settings['hncgnt0.67-hncinit'])
    votca_settings['shncgnt0.67-hncinit']['meta']['all-interactions'] = False
    votca_settings['shncgnt0.67-hncinit']['meta']['selected-interactions'] = True
    del votca_settings['shncgnt0.67-hncinit']['inverse']['gauss_newton']['pressure_constraint']
    
    # selective-t-HNCGN x 0.67 no constraint average init
    votca_settings['shncgnt0.67-avginit'] = copy.deepcopy(votca_settings['shncgnt0.67-hncinit'])
    votca_settings['shncgnt0.67-avginit']['inverse']['initial_guess'] = {'method': 'table',
                                                                         'cut_off': ('cut', lambda x: x),
                                                                        } 
    # selective-t-HNCGN x 0.67 no constraint average init
    votca_settings['shncgnt0.67-ibiinit'] = copy.deepcopy(votca_settings['shncgnt0.67-hncinit'])
    votca_settings['shncgnt0.67-ibiinit']['meta']['only-fg-sys-type'] = [
        'mix-ethanol+pyridine',
        'mix-ethylene_glycol+tert-butanol',
        'mix-ethylene_glycol+pyridine',
        'mix-acetone+pyridine',
        'mix-acetone+diethyl_ether',
        'mix-diethyl_ether+ethylene_glycol',
        'mix-ethyl_acetate+pyridine',
    ]
    votca_settings['shncgnt0.67-ibiinit']['inverse']['initial_guess'] = {'method': 'table',
                                                                         'cut_off': ('cut', lambda x: x),
                                                                        } 
    # selective-t-HNCGN x 0.67 no constraint expoential init
    """
    votca_settings['shncgnt0.67-expinit'] = copy.deepcopy(votca_settings['shncgnt0.67-hncinit'])
    votca_settings['shncgnt0.67-expinit']['meta']['max_step0'] = ('cut_gn_res', lambda x: x)
    votca_settings['shncgnt0.67-expinit']['inverse']['initial_guess'] = {'method': 'table',
                                                                         'cut_off': ('cut', lambda x: x),
                                                                        } 
    """
    """
    # selective-HNCGN x 0.67 no constraint
    votca_settings['shncgn0.67-hncinit'] = copy.deepcopy(votca_settings['shncgnt0.67-hncinit'])
    votca_settings['shncgn0.67-hncinit']['non-bonded']['max'] = ('cut_gn_res', lambda x: 2 * x)
    votca_settings['shncgn0.67-hncinit']['inverse']['iie']['use_target_dcdh'] = 'false'
    
    # selective-HNCGN x 0.67 no constraint exponential init
    votca_settings['shncgn0.67-expinit'] = copy.deepcopy(votca_settings['shncgn0.67-hncinit'])
    votca_settings['shncgn0.67-expinit']['meta']['max_step0'] = ('cut_gn_res', lambda x: x)
    votca_settings['shncgn0.67-expinit']['inverse']['initial_guess'] = {'method': 'table',
                                                                         'cut_off': ('cut', lambda x: x),
                                                                        } 
    """
    
    # selective-HNCGN x 0.67 no constraint
    #votca_settings['shncgn0.67-hncinit'] = copy.deepcopy(votca_settings['shncgnt-hncinit'])
    #votca_settings['shncgn0.67-hncinit']['non-bonded']['max'] = ('cut_gn_res', lambda x: 2 * x)
    
    return votca_settings

votca_settings = gen_votca_settings()
votca_settings.keys()

### combination specific settings

In [ ]:
combination_settings = {
    'interaction-votca-settings': {
        # fg_sys_type state mapping votca_setting. None is wildcard, list means do multiple
        #("mwater-argon", None, "unity+mw", None): [  # do not update mWater potential
            #{'type': 'substitute', 'path': ['non-bonded', 'MW-MW', 'improve_dist_near_core'], 'value': ""},
            #{'type': 'substitute', 'path': ['non-bonded', 'MW-MW', 'inverse'], 'value': {
                #'do_potential': "0",
                #'is_target_distribution': "false",
                #'imc': {'group': 'none'},
            #}},
        #],
        #("mix-ethanol+tert-butanol", "xrange2", "1bead", None): [
            #{'type': 'substitute', 'path': ['non-bonded', 'B-B', 'improve_dist_near_core', 'fit_end_g'], 'value': "0.5"},
        #],
        ("tert-butanol", "pure", "1bead", None): [
            {'type': 'substitute', 'path': ['non-bonded', 'A-A', 'improve_dist_near_core', 'fit_start_g'], 'value': "1e-5"},
            {'type': 'substitute', 'path': ['non-bonded', 'A-A', 'improve_dist_near_core', 'fit_end_g'], 'value': "0.5"},
        ],
        (None, "x0.5", "1bead", None): [
            {'type': 'substitute', 'path': ['non-bonded', 'A-A', 'inverse', 'do_potential'], 'value': "0"},
            {'type': 'substitute', 'path': ['non-bonded', 'B-B', 'inverse', 'do_potential'], 'value': "0"},
            {'type': 'substitute', 'path': ['non-bonded', 'A-A', 'inverse', 'is_target_distribution'], 'value': "false"},
            {'type': 'substitute', 'path': ['non-bonded', 'B-B', 'inverse', 'is_target_distribution'], 'value': "false"},
        ],
    }
}

### cg problem generators

In [ ]:
# this function generates cg_setup['interaction-votca-settings'] for per-interaction votca settings
def gen_interaction_votca_settings(fg_sys_type_key, state_key, mapping_key, votca_setting_key, combination_interaction_votca_settings):
    
    interaction_votca_settings = {}
    input_parameters = (fg_sys_type_key, state_key, mapping_key, votca_setting_key)
    for setting_combination, adaptions in {k: v for k, v in combination_interaction_votca_settings.items()
                                           # going throuth those setting_combinations that fit the the parameters
                                          if all((key_param == key_comb or key_comb is None) for key_param, key_comb in zip(input_parameters, k))}.items():
        for adaption in (a for a in adaptions if a['type'] == 'substitute'):
            change_dict_tree_with_path(interaction_votca_settings, adaption['path'], adaption['value'])
    
    return interaction_votca_settings

In [ ]:
def is_combination_runnable(fg_sys_type_key, fg_sys_type, state_key, state, mapping_key, mapping, cg_sys_types, votca_setting_key, votca_setting, combination_settings):
    
    def _by_selected_interactions(fg_sys_type_key, state_key, mapping_key, votca_setting_key, votca_setting, combination_interaction_votca_settings):
        interaction_votca_settings = gen_interaction_votca_settings(fg_sys_type_key, state_key, mapping_key, votca_setting_key, combination_interaction_votca_settings)
        path = ['non-bonded', None, 'inverse', 'do_potential']
        has_do_potential_0 = any((v == '0' for v in get_values_in_dict_tree(interaction_votca_settings, path)))
        selected_meta_key = {True: 'selected-interactions', False: 'all-interactions'}[has_do_potential_0]
        return votca_setting['meta'][selected_meta_key]
    
    def _by_multistate(fg_sys_type_key, state, votca_setting):
        return votca_setting['meta'][f"{state['type']}state"]
    
    def _by_tag_disabled(fg_sys_type, state, mapping, cg_sys_type, votca_setting):
        for type_ in (fg_sys_type, state, mapping, cg_sys_type, votca_setting):
            if 'disabled' in type_['tags']:
                return False
        return True
    
    def _by_only_fg_sys_type(votca_setting, fg_sys_type_key):
        if 'only-fg-sys-type' in votca_setting['meta']:
            return fg_sys_type_key in votca_setting['meta']['only-fg-sys-type']
        return True
                    
        
    return all((
        _by_selected_interactions(fg_sys_type_key, state_key, mapping_key, votca_setting_key, votca_setting, combination_settings['interaction-votca-settings']),
        _by_multistate(fg_sys_type_key, state, votca_setting),
        _by_tag_disabled(fg_sys_type, state, mapping, cg_sys_types[(fg_sys_type_key, mapping_key)], votca_setting),
        _by_only_fg_sys_type(votca_setting, fg_sys_type_key),
    ))

In [ ]:
def cg_setup_generator(fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=False, return_indices=False,
                       print_keys=True, combination_settings=combination_settings):
    for f, (fg_sys_type_key, fg_sys_type) in enumerate(fg_sys_types.items()):
        if print_keys: print(f, fg_sys_type_key)
        for s, (state_key, state) in enumerate({state_key: state for state_key, state in states.items()
                                                if fg_sys_type_key in state.keys()}.items()):
            if print_keys: print('', s, state_key)
            for m, (mapping_key, mapping) in enumerate({mapping_key: mapping for mapping_key, mapping in mappings.items()
                                                        # filter for keys of cg_sys_types
                                                        if (fg_sys_type_key, mapping_key) in cg_sys_types.keys()}.items()):
                if print_keys: print(' ', m, mapping_key)
                v = -1
                for votca_setting_key, votca_setting in votca_settings.items():
                    if not is_combination_runnable(fg_sys_type_key, fg_sys_type, state_key, state[fg_sys_type_key], mapping_key, mapping, cg_sys_types, votca_setting_key, votca_setting, combination_settings):
                        continue
                    v += 1
                    if print_keys: print('  ', v, votca_setting_key)
                    cg_setup = {}
                    cg_setup['name'] = '-'.join((fg_sys_type_key, state_key, mapping_key, votca_setting_key))
                    cg_setup['folder'] = '/'.join((fg_sys_type_key, state_key, mapping_key, votca_setting_key))
                    cg_setup['tgt-dist-folder'] = os.path.normpath(os.path.join(cg_setup['folder'], '..', 'target-dists'))
                    cg_setup['fg-topology'] = fg_sys_type['topology']
                    cg_setup['fg-md-settings'] = fg_sys_type['md-settings']
                    cg_setup['state'] = state[fg_sys_type_key]
                    cg_setup['mapping'] = gen_mapping(fg_sys_type_key, mappings, mapping_key)
                    cg_setup['cg-sys-type'] = cg_sys_types[(fg_sys_type_key, mapping_key)]
                    cg_setup['cg-topology'] = cg_sys_types[(fg_sys_type_key, mapping_key)]['topology']
                    cg_setup['cg-md-settings'] = cg_sys_types[(fg_sys_type_key, mapping_key)]['md-settings']
                    cg_setup['votca-settings'] = copy.deepcopy(votca_setting)
                    
                    # apply per cg-sys-type votca-settings
                    if 'votca-settings' in cg_setup['cg-sys-type'].keys():
                        cg_setup['votca-settings'] = replace_dict_tree(cg_setup['votca-settings'], cg_sys_types[(fg_sys_type_key, mapping_key)]['votca-settings'])
                    # apply functional per cg-sys-type votca settings
                    cg_setup['votca-settings'] = apply_and_replace_string_function_tuples(cg_setup['votca-settings'], cg_sys_types[(fg_sys_type_key, mapping_key)]['functional-votca-settings-input'])
                    # apply per state votca-settings
                    if 'votca-settings' in cg_setup['state'].keys():
                        cg_setup['votca-settings'] = replace_dict_tree(cg_setup['votca-settings'], cg_setup['state']['votca-settings'], create_non_existing=False)
                        
                    # these will be picked up by cg.gen_votca_settings()
                    cg_setup['interaction-votca-settings'] = gen_interaction_votca_settings(fg_sys_type_key, state_key, mapping_key, votca_setting_key, combination_settings['interaction-votca-settings'])
                    
                    returns = [cg_setup]
                    if return_keys:
                        returns.extend((fg_sys_type_key, state_key, mapping_key, votca_setting_key))
                    if return_indices:
                        returns.extend((f, s, m, v))
                    if len(returns) == 1:
                        yield returns[0]
                    else:
                        yield tuple(returns)
                
                
list(cg_setup_generator(fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True, return_indices=True,
                        print_keys=True));


In [ ]:
def cg_setup_selector(fg_sys_types, states, mappings, cg_sys_types, votca_settings, fg_sys_type_key, state_key, mapping_key, votca_setting_key, combination_settings=combination_settings):
    """Return a single cg_setup"""
    cg_problem_selected = next(cg_setup_generator(
        {fg_sys_type_key: fg_sys_types[fg_sys_type_key]},
        {state_key: states[state_key]},
        {mapping_key: mappings[mapping_key]},
        cg_sys_types,
        {votca_setting_key: votca_settings[votca_setting_key]},
        return_keys=False, return_indices=False, print_keys=False
    ))
    return cg_problem_selected

cg_setup_selector(fg_sys_types, states, mappings, cg_sys_types, votca_settings, 'ethanol', 'pure', '1bead', 'hncnt-hncinit', combination_settings=combination_settings)['name']

In [ ]:
def md_iterator(fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=False, print_keys=True):
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True, return_indices=True, print_keys=False):
        if m == 0 and v == 0:  # once for each state
            if print_keys:
                print(f, fg_sys_type_key)
                print('', s, state_key)
            working_dir_md = os.path.join(fg_sys_type_key, state_key, 'fg')
            statepoints = gen_statepoints(cg_problem['state'])
            if return_keys:
                yield cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md
            else:
                yield cg_problem, statepoints, working_dir_md

In [ ]:
def test_md_iterator():
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True):
        pass
        
test_md_iterator()

In [ ]:
def test_groupby():
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['octane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['hncn-ibiintra-hncinit', 'hncnt-ibiintra-hncinit']}
    
    for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                              key=lambda x: (x[1], x[2], x[3])):
        print(fg_sys_type_key, state_key, mapping_key)
        for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
            print(' ', votca_setting_key)
        
        
test_groupby()

# Generage coarse-graining files

generate those files needed for calculating the target distributions here

## check charges

In [ ]:
def check_charges():
    votca_settings_to_do = {key: votca_settings[key] for key in ['hncgnt-hncinit']}
    for cg_problem in cg_setup_generator(fg_sys_types, states, mappings, cg_sys_types, votca_settings_to_do, print_keys=False):
        cg.print_fg_mol_charge(cg_problem)

check_charges()

## generate mapping files

In [ ]:
def gen_mapping_files():
    for cg_problem in cg_setup_generator(fg_sys_types, states, mappings, cg_sys_types, votca_settings, print_keys=True):
        for moltype in cg_problem['mapping']['moltypes'].keys():
            # for some molecules we want more exclusion in the mapping file
            if 'bonds-mapping-only' in cg_problem['cg-topology']['moltypes'][moltype]:
                cg_problem_temp = copy.deepcopy(cg_problem)
                cg_problem_temp['cg-topology']['moltypes'][moltype]['bonds'] = cg_problem_temp['cg-topology']['moltypes'][moltype]['bonds-mapping-only']
                print('FOO')
            else:
                cg_problem_temp = cg_problem
            #print('   ', moltype)
            mapping_xml = cg.gen_votca_mapping(cg_problem_temp, moltype)
            mapping_unity_xml = cg.gen_votca_mapping(cg_problem_temp, moltype, cg_unity=True)
            with WorkingDir(cg_problem_temp['folder']):
                mapping_xml.write(f"map-{moltype}.xml")
                mapping_unity_xml.write(f"map-cgunity-{moltype}.xml")

gen_mapping_files()

## generate settings{,_step0}.xml

In [ ]:
def gen_settings():
    for cg_problem in cg_setup_generator(fg_sys_types, states, mappings, cg_sys_types, votca_settings):
        
        # generate settings.xml
        settings_xml = cg.gen_votca_settings(cg_problem)
        with WorkingDir(cg_problem['folder']):
            settings_xml.write(f"settings.xml")
        
        # check if settings_step0.xml needed
        max_ = cg_problem['votca-settings']['non-bonded']['max']
        max_0 = cg_problem['votca-settings']['meta']['max_step0']
        step0_different = max_ != max_0
        
        # generate settings_step0.xml if needed
        if step0_different:
            #print(max_, max_0)
            cg_problem_step0 = copy.deepcopy(cg_problem)
            cg_problem_step0['votca-settings']['non-bonded']['max'] = cg_problem_step0['votca-settings']['meta']['max_step0']
            cg_problem_step0['votca-settings']['inverse']['iterations_max'] = 0
            settings_step0_xml = cg.gen_votca_settings(cg_problem_step0)
            with WorkingDir(cg_problem['folder']):
                settings_step0_xml.write(f"settings_step0.xml")
        else:
            with WorkingDir(cg_problem['folder']):
                run_bash('rm -f settings_step0.xml')

gen_settings()

## generate fine-grained topology.xml

In [ ]:
def gen_xml_topol_fg():
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True):
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            with WorkingDir(os.path.join(working_dir_md, statepoint['path'])):
                xml_top = cg.gen_topol_xml_fg(cg_problem, statepoint)
                xml_top.write('topology.xml')
            
gen_xml_topol_fg()

# Fine-grained MD

## prepare

### check itp files

In [ ]:
# acetone misses some dihedrals, ignoreing it because rotation of methyl group not important for CG
def check_itp():
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True):
        if cg_problem['fg-md-settings']['md-program'] == 'gromacs':
            template_dir = os.path.abspath('template')
            for moltype in cg_problem['fg-topology']['moltypes'].values():
                itp_file = f"{template_dir}/itp/{cg_problem['fg-topology']['ff-key']}/{moltype['itp']}"
                bonds = gt.itp.get_bonds(itp_file)
                print(gt.itp.pairs_from_bonds(bonds) == gt.itp.get_pairs(itp_file), end=' ')
                print(gt.itp.angles_from_bonds(bonds) == gt.itp.get_angles(itp_file), end=' ')
                print(gt.itp.dihedrals_from_bonds(bonds) == gt.itp.get_dihedrals(itp_file))
        else:
            print('.. not Gromacs ..')
    
check_itp()

### prepare MD Gromacs

In [ ]:
def prepare_md_gromacs():
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        {k: v for k, v in fg_sys_types.items() if v['md-settings']['md-program'] == 'gromacs'},
        states, mappings, cg_sys_types, votca_settings, return_keys=True):
        
        # iterate statepoints, only one for type == 'single'
        for statepoint in statepoints:
            print(' ', statepoint['path'])
            working_dir = os.path.join(working_dir_md, statepoint['path'])
            template_dir = os.path.abspath('template')
            with WorkingDir(working_dir):
                # make dir topol
                run_bash("mkdir -p topol")
                # itp files
                for moltype in cg_problem['fg-topology']['moltypes'].values():
                    run_bash(f"cp {template_dir}/itp/{cg_problem['fg-topology']['ff-key']}/{moltype['itp']} topol/")
                topol_moltype_includes = '\n'.join([f'#include "{moltype["itp"]}"' for moltype in cg_problem['fg-topology']['moltypes'].values()])
                topol_molecules = '\n'.join([f"{moltype['short-name']}  {statepoint['composition'][moltype_key]}" for moltype_key, moltype in cg_problem['fg-topology']['moltypes'].items()
                                            if statepoint['composition'][moltype_key] > 0])
                # if there is a forcefield.itp in the template folder (madrid)
                if os.path.exists(f"{template_dir}/itp/{cg_problem['fg-topology']['ff-key']}/forcefield.itp"):
                    run_bash(f"cp {template_dir}/itp/{cg_problem['fg-topology']['ff-key']}/forcefield.itp topol/")
                    topol = '#include "forcefield.itp"'
                else:  # if not link to gromacs shared files (oplsaa.ff)
                    topol = f"#include \"{cg_problem['fg-topology']['ff-key']}/forcefield.itp\""
                topol += f"""
{topol_moltype_includes}

[ system ]
{fg_sys_type_key}

[ molecules ]
{topol_molecules}
"""
                with open('topol/topol.top', 'w') as f:
                    f.write(topol)
                # mdp files
                # NPT
                if 'pressure-fg' in statepoint.keys():
                    stages = ['equi1', 'equi2', 'equi3', 'prod']
                    # make dirs
                    run_bash("mkdir -p " + ' '.join(stages))
                    # copy from template
                    for stage in stages:
                        run_bash(f"cp {template_dir}/mdp/fg-npt/{cg_problem['fg-md-settings']['integrator+thermostat']}/{stage}.mdp {stage}/grompp.mdp")
                    # mdp run length
                    gt.mdp.set_parameter("equi1/grompp.mdp", 'nsteps',    10_000)
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'nsteps',   100_000)
                    gt.mdp.set_parameter("equi3/grompp.mdp", 'nsteps', 2_000_000)
                    gt.mdp.set_parameter("prod/grompp.mdp",  'nsteps', 2_000_000)
                    # output
                    gt.mdp.set_parameter("prod/grompp.mdp", 'nstxout-compressed', 100 if 'is-large' in states[state_key][fg_sys_type_key]['tags'] else 10)
                    # mdp temperature, pressure
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'gen-temp', statepoint['temperature'])
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'ref-t', statepoint['temperature'])
                    gt.mdp.set_parameter("equi3/grompp.mdp", 'ref-t', statepoint['temperature'])
                    gt.mdp.set_parameter("prod/grompp.mdp", 'ref-t', statepoint['temperature'])
                    gt.mdp.set_parameter("equi3/grompp.mdp", 'ref-p', statepoint['pressure-fg'])
                    gt.mdp.set_parameter("prod/grompp.mdp", 'ref-p', statepoint['pressure-fg'])
                    # mdp dt, tau-t, tau-p
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'dt', cg_problem['fg-md-settings']['dt'])
                    gt.mdp.set_parameter("equi3/grompp.mdp", 'dt', cg_problem['fg-md-settings']['dt'])
                    gt.mdp.set_parameter("prod/grompp.mdp", 'dt', cg_problem['fg-md-settings']['dt'])
                    gt.mdp.set_parameter("equi2/grompp.mdp", 'tau-t', cg_problem['fg-md-settings']['tau-t'])
                    gt.mdp.set_parameter("equi3/grompp.mdp", 'tau-t', cg_problem['fg-md-settings']['tau-t'])
                    gt.mdp.set_parameter("prod/grompp.mdp", 'tau-t', cg_problem['fg-md-settings']['tau-t'])
                    gt.mdp.set_parameter("equi3/grompp.mdp", 'tau-p', cg_problem['fg-md-settings']['tau-p'] / 2)  # faster equilibration
                    gt.mdp.set_parameter("prod/grompp.mdp", 'tau-p', cg_problem['fg-md-settings']['tau-p'])
                else:
                    raise Exception('other ensembles not implemented here')
                # gro files
                for moltype_key in cg_problem['fg-topology']['moltypes'].keys():
                    run_bash(f"cp {template_dir}/gro/fg/single-{moltype_key}.gro equi1/")
                # mdp change columbtype if all charges close to zero
                charges = [bead['charge']
                           for mt in cg_problem['fg-topology']['moltypes'].values()
                           for bead in mt['beads'].values()]
                if np.allclose(charges, np.zeros_like(charges)):
                    for stage in stages:
                        gt.mdp.set_parameter(f"{stage}/grompp.mdp", 'coulombtype', 'Cut-off')
                
prepare_md_gromacs()

### fill box

- https://en.wikipedia.org/wiki/Ethanol
- https://en.wikipedia.org/wiki/2-Butanol
- https://en.wikipedia.org/wiki/Tert-Butyl_alcohol
- https://en.wikipedia.org/wiki/Ethylene_glycol
- https://en.wikipedia.org/wiki/Acetone
- https://en.wikipedia.org/wiki/Pyridine
- https://en.wikipedia.org/wiki/Diethyl_ether
- https://en.wikipedia.org/wiki/1,4-Dioxane
- https://en.wikipedia.org/wiki/Ethyl_acetate

In [ ]:
def fill_box_gromacs():
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['pyridine']}
    
    insert_try_scale = collections.defaultdict(lambda: (200, 0.42), {
        #"mix-diethyl_ether+pyridine": (400, 0.42),
    })
    
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        {k: v for k, v in fg_sys_types_to_do.items() if v['md-settings']['md-program'] == 'gromacs'},
        states, mappings, cg_sys_types, votca_settings, return_keys=True):
        # iterate statepoints, only one for type == 'single'
        for statepoint in statepoints:
            print(' ', statepoint['path'])
            working_dir = os.path.join(working_dir_md, statepoint['path'])
            with WorkingDir(working_dir):

                # required format for gromacstools.top
                moltype_list = gen_moltype_list(cg_problem['fg-topology'], statepoint)
                top = gt.top.Topology()
                top.load_simple_top(moltype_list)
                
                # Volume
                if 'pressure-fg' in statepoint.keys():
                    if len(statepoint['composition']) == 1:
                        volume = top.mass() / const.N_A / molecules[fg_sys_type_key]['density-exp']
                    else:
                        # use weighted average
                        volume = 0
                        n_mols_total = 0
                        for mol, n_mols in statepoint['composition'].items():
                            n_mols_total += n_mols
                            volume += n_mols * top.mass() / const.N_A / mol['density-exp']
                        volume /= n_mols_total
                        cg_problem
                    volume *=  1e21  # from ml to nm^3
                    volume *= 1.30  # start with lower density for easier inserting
                    box_edge = volume**(1/3)
                elif 'volume-fg' in statepoint.keys():
                    volume = statepoint['volume-fg']
                    box_edge = volume**(1/3)
                else:
                    raise Exception('other ensembles not implemented here')
                print('volume:', volume)
                print('edge:', volume**(1/3))

                # check existing
                if os.path.exists("equi1/conf.gro"):
                    n_atoms_present = gt.gro.get_natoms("equi1/conf.gro")
                    box_present = gt.gro.get_box("equi1/conf.gro")
                    n_atoms_wanted = top.natoms()
                    if n_atoms_present == n_atoms_wanted and np.allclose(box_present, [box_edge]*3):
                        print("..suitable conf.gro found, skipping..")
                        continue

                # empty box with volume
                empty_gro = f"system\n0\n{box_edge} {box_edge} {box_edge}"
                with open("equi1/conf.gro", 'w') as f:
                    f.write(empty_gro)

                # insert molecules
                for moltype in moltype_list:
                    n_mols = moltype['nmols']
                    mt_name = moltype['name']
                    try_, scale = insert_try_scale[fg_sys_type_key]
                    run_bash(f"gmx -quiet insert-molecules -f equi1/conf.gro -o equi1/conf.gro -ci equi1/single-{mt_name}.gro -nmol {n_mols} -try {try_} -scale {scale}")
                    run_bash("rm -f equi1/\#conf.gro.*")

                # check
                n_atoms_inserted = gt.gro.get_natoms("equi1/conf.gro")
                n_atoms_wanted = top.natoms()
                if n_atoms_inserted != n_atoms_wanted:
                    print(n_atoms_inserted, n_atoms_wanted)
                    raise Exception("not enough molecules inserted")
                    
fill_box_gromacs()

### prepare target-dists folder

In [ ]:
def prepare_tgt_dists_folder():
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['water-spce']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['x0.1']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['mshncgnt-ibiintra-hncinit']}
    
    # iterate fg, state, mapping
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in (data for data in cg_setup_generator(
        fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True, return_indices=True, print_keys=False,
    ) if data[8] == 0):
                    
        # find votca-setting largest max
        votca_setting_key_largest_max = None
        largest_max = 0
        # iterate votca settings
        for cg_problem_temp, _, _, _, votca_setting_key  in cg_setup_generator(
            {fg_sys_type_key: fg_sys_types[fg_sys_type_key]},
            {state_key: states[state_key]},
            {mapping_key: mappings[mapping_key]},
            cg_sys_types, votca_settings, return_keys=True, 
        ):
            # only looking at non-bonded.max, bonded should be the same in all votca-settings
            max0_max = {field2: cg_problem_temp['votca-settings'][field1][field2] for field1, field2 in (('non-bonded', 'max'), ('meta', 'max_step0'))}
            if largest_max < max(max0_max.values()):
                print('higher!')
                largest_max = max(max0_max.values())
                votca_setting_key_largest_max = (votca_setting_key, max(max0_max, key=max0_max.get))

        print('largest max in:', votca_setting_key_largest_max)
                
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            
            # mkdir and copy
            dir_tgt_dists = cg_problem['tgt-dist-folder']
            run_bash(f"mkdir -p {dir_tgt_dists}/{statepoint['path']}")
            dir_max = os.path.normpath(os.path.join(cg_problem['folder'], '..', votca_setting_key_largest_max[0]))
            settings_file = f"settings{votca_setting_key_largest_max[1].split('max')[-1]}.xml"
            run_bash(f"cp {dir_max}/{settings_file} {dir_tgt_dists}/settings.xml")
            for moltype in cg_problem['mapping']['moltypes'].keys():
                run_bash(f"cp {dir_max}/map-{moltype}.xml {dir_tgt_dists}/")
            
                        
prepare_tgt_dists_folder()

## run

### run MD and calculate distributions

In [ ]:
def run_md_dist(copy_only=False, run_if_dist_present=False):
    remote_partition = 'batchgpu'
    remote_dir_base, remote_header, remote_footer, remote_args = gen_remote_stuff(remote_host, remote_partition, ntasks=48, votca=True, gres='gpu:1')
    
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['ethanol']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['pure-large']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['mshncgnt-ibiintra-hncinit']}
    
    # iterate md setups
    for cg_problem_md, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True):
        
        md_program = cg_problem_md['fg-md-settings']['md-program']
        assert md_program in ('gromacs',)
        
        statepoints = gen_statepoints(cg_problem_md['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            working_dir_md = os.path.join(fg_sys_type_key, state_key, 'fg', statepoint['path'])
            remote_dir_md = os.path.join(remote_dir_base, working_dir_md)
            run_bash(f"ssh {remote_host} mkdir -p {remote_dir_md}")
            # copy simulation files to remote
            if md_program == 'gromacs':
                filelist = ["equi1/conf.gro", "*/grompp.mdp", "topol"]
            with WorkingDir(working_dir_md):
                gt.remote.push_files(filelist, remote_host, remote_dir_md)
            # check some dists are there already
            dists_done = all((glob.glob(os.path.join(cg_problem['tgt-dist-folder'], statepoint['path'], '*.dist.tgt'))
                              for cg_problem, f, s, m, v in cg_setup_generator(
                                  {fg_sys_type_key: fg_sys_types[fg_sys_type_key]},
                                  {state_key: states[state_key]},
                                  mappings, cg_sys_types, votca_settings,
                                  return_keys=False, return_indices=True, print_keys=False)
                              if v == 0))
            if dists_done:
                print('.. all target dists already present ..')
                if not run_if_dist_present:
                    continue
                
            if md_program == 'gromacs':
                mdrun_nt = remote_args['ntasks']
                mdrun_steep_flag = {
                    'batch': f"-nt {mdrun_nt}",
                    'batchgpu': f"-nt {mdrun_nt}",
                    'milan': f"-nt {mdrun_nt}",
                    'rtx3080': f"-nt {mdrun_nt}",
                }[remote_partition]
                mdrun_flag = {
                    'batch': f"-nt {mdrun_nt}",
                    'batchgpu': f"-nt {mdrun_nt} -update gpu",
                    'milan': f"-nt {mdrun_nt}",
                    'rtx3080': f"-nt {mdrun_nt} -update gpu",
                }[remote_partition]
                mdrun_flag += ' -pin on'
            local_folder = "$JOBTMP"
            # one script per md statepoint for all cg problems
            if copy_only:
                script = remote_header
            elif md_program == 'gromacs':
                script = remote_header + fr"""
pushd {remote_dir_md}
pushd equi1
    if [[ ! -f confout.gro ]]; then
        gmx grompp -p ../topol/topol.top -maxwarn 1  # FLEXIBLE might not be defined in some topologies
        gmx mdrun {mdrun_steep_flag}
    fi
    rm -f \#*
popd

pushd equi2
    if [[ ! -f confout.gro ]]; then
        gmx grompp -p ../topol/topol.top -c ../equi1/confout.gro
        gmx mdrun {mdrun_flag}
    fi
    rm -f \#*
popd

if [[ -f equi3/grompp.mdp ]]; then
pushd equi3
    if [[ ! -f confout.gro ]]; then
        gmx grompp -p ../topol/topol.top -c ../equi2/confout.gro
        gmx mdrun {mdrun_flag}
    fi
    rm -f \#*
popd
fi

[[ -f equi3/confout.gro ]] && last_conf=equi3/confout.gro || last_conf=equi2/confout.gro
pushd prod
    gmx grompp -p ../topol/topol.top -c ../$last_conf
    gmx mdrun {mdrun_flag} -x {local_folder}/traj_comp.xtc
    rm -f \#*
popd
popd

# load gromacs version of spack
spack unload gromacs
spack load $spack_gmx_for_votca

# generate tpr for votca
gmx grompp -f prod/grompp.mdp -p topol/topol.top -c $last_conf -o topol/topol-gmx-votca.tpr
rm -f topol/\#topol* mdout.mdp
"""
            # stay in statepoint but iterate mappings
            for cg_problem_td in (data[0] for data in cg_setup_generator(
                {fg_sys_type_key: fg_sys_types[fg_sys_type_key]},
                {state_key: states[state_key]},
                mappings, cg_sys_types, votca_settings, return_keys=True, print_keys=False, return_indices=True,
            ) if data[8] == 0):
                
                working_dir_td = os.path.join(cg_problem_td['tgt-dist-folder'])
                working_dir_td_state = os.path.join(cg_problem_td['tgt-dist-folder'], statepoint['path'])
                remote_dir_td = os.path.join(remote_dir_base, working_dir_td)
                remote_dir_td_state = os.path.join(remote_dir_base, working_dir_td_state)
                # mkdir
                run_bash(f"ssh {remote_host} mkdir -p {remote_dir_td_state}")
                # copy simulation files to remote
                with WorkingDir(working_dir_td):
                    filelist = ["settings.xml", "map-*.xml"]
                    gt.remote.push_files(filelist, remote_host, remote_dir_td)
                    mapping_files = ';'.join(f"{remote_dir_td}/map-{moltype_key}.xml" for moltype_key in cg_problem_td['fg-topology']['moltypes'].keys())
                    if copy_only:
                        pass
                    elif md_program == 'gromacs':
                        script += fr"""
pushd {remote_dir_td_state}
    csg_stat --top {remote_dir_md}/topol/topol-gmx-votca.tpr --options {remote_dir_td}/settings.xml --trj {local_folder}/traj_comp.xtc \
        --cg "{mapping_files}" --nt=$SLURM_JOB_CPUS_PER_NODE --ext dist.tgt
"""
            # submit job
            script += remote_footer
            with WorkingDir(working_dir_md):
                jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir_md, dry_run=False)
            print(jobid)
            if jobid != None:
                jobids.append(jobid)

run_md_dist(copy_only=False)

### check job status

In [ ]:
jobids = check_job_stati(jobids, remote_host)

### pull MD files from cluster

In [ ]:
def pull_md():
    remote_dir_base, remote_header, remote_footer, remote_args = gen_remote_stuff(remote_host, 'batchgpu', ntasks=48, votca=True, gres='gpu:1')
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['pyridine']}
    
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        fg_sys_types_to_do, states, mappings, cg_sys_types, votca_settings, return_keys=True):
        
        md_program = cg_problem['fg-md-settings']['md-program']
        assert md_program in ('gromacs', 'lammps')
        
        # iterate statepoints, only one for type == 'single'
        for statepoint in statepoints:
            print(' ', statepoint['path'])
            working_dir = os.path.join(working_dir_md, statepoint['path'])
            remote_dir = os.path.join(remote_dir_base, working_dir)
            with WorkingDir(working_dir):
                if md_program == 'gromacs':
                    filelist = ["*/*.edr", "*/confout.gro", "*/topol.tpr", "topol/topol-gmx-votca.tpr"]
                    exclude = "traj*"
                elif md_program == 'lammps':
                    filelist = ["*-out.lammpstrj", "prod-out.data", "log.lammps"]
                    exclude = "traj*"
                gt.remote.pull_files(filelist, remote_host, remote_dir, exclude=exclude)
                
pull_md()

### equilibration check

In [ ]:
def show_energy_graphs(properties_list, edr_file="ener.edr"):
    run_bash("gmx energy -f {} -o energy-temp.xvg <<< '{}'".format(edr_file, "\n".join(properties_list)))
    gt.xvg.plot("energy-temp.xvg")
    run_bash("rm energy-temp.xvg")

In [ ]:
def check_equi_md():
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['ethanol']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['Vrange3']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['mshncgnt-ibiintra-hncinit']}
    
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True):
        # iterate statepoints, only one for type == 'single'
        for statepoint in statepoints:
            print(' ', statepoint['path'])
            working_dir = os.path.join(working_dir_md, statepoint['path'])
            with WorkingDir(working_dir):
                try:
                    print("equilibration 3")
                    #show_energy_graphs(["Temperature"], edr_file="equi3/ener.edr")
                    #show_energy_graphs(["Pressure"], edr_file="equi3/ener.edr")
                    show_energy_graphs(["Volume"], edr_file="equi3/ener.edr")
                    #print("production")
                    #show_energy_graphs(["Temperature"], edr_file="prod/ener.edr")
                    #show_energy_graphs(["Pressure"], edr_file="prod/ener.edr")
                    #show_energy_graphs(["Volume"], edr_file="prod/ener.edr")
                except:
                    print('.. no data ..')
                
check_equi_md()

### check density

In [ ]:
def check_density():
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['ethanol']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['mshncgnt-ibiintra-hncinit']}
    
    for cg_problem, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True):
        # iterate statepoints, only one for type == 'single'
        for statepoint in statepoints:
            print(' ', statepoint['path'])
            working_dir = os.path.join(working_dir_md, statepoint['path'])
            with WorkingDir(working_dir):
                
                run_bash("gmx energy -f prod/ener.edr -o /tmp/energy-temp.xvg <<< 'Density'")
                data, _ = gt.xvg.load("/tmp/energy-temp.xvg")
                run_bash("rm /tmp/energy-temp.xvg")
                density = data['Density'].mean() / 1000
                print(density / molecules[fg_sys_type_key]['density-exp'])
                
                moltype_list = gen_moltype_list(cg_problem['fg-topology'], statepoint)
                top = gt.top.Topology()
                top.load_simple_top(moltype_list)
                
                volume = top.mass() / const.N_A / molecules[fg_sys_type_key]['density-exp'] * 1e21
                volume *= 0.9
                box_x = volume**(1/3)
                box_x_floor = np.floor(box_x / 0.2) * 0.2
                box_x_test = (volume * 10000 / 3000)**(1/3)
                box_x_test_floor = np.floor(box_x_test / 0.2) * 0.2
                print(box_x, box_x_floor)
                run_bash("gmx energy -f prod/ener.edr -o /tmp/energy-temp.xvg <<< 'Box-X'")
                data, _ = gt.xvg.load("/tmp/energy-temp.xvg")
                run_bash("rm /tmp/energy-temp.xvg")
                print(data['Box-X'].min(), box_x_floor)
                print(box_x_test_floor)
                
check_density()

### pull dist files from cluster

In [ ]:
def pull_dist():
    remote_dir_base, remote_header, remote_footer, remote_args = gen_remote_stuff(remote_host, 'batchgpu', ntasks=48, votca=True, gres='gpu:1')
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['pyridine']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    # iterate fg, state, mapping
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in (data for data in cg_setup_generator(
        fg_sys_types_to_do, states, mappings_to_do, cg_sys_types, votca_settings, return_keys=True, return_indices=True, print_keys=False,
    ) if data[8] == 0):
        print(cg_problem['name'])
        
        # iterate state points
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            #print('   ', statepoint['path'])
            
            working_dir = os.path.join(cg_problem['tgt-dist-folder'], statepoint['path'])
            remote_dir = os.path.join(remote_dir_base, working_dir)
            with WorkingDir(working_dir):
                filelist = ["*.dist.tgt", "*.dist-intra.tgt"]
                exclude = "traj*"
                # does never fail
                gt.remote.pull_files(filelist, remote_host, remote_dir, exclude=exclude)
                if len(glob.glob("*.tgt")) == 0:
                    print('.. no data ..')
                
pull_dist()

# Iterative coarse-graining

## prepare

### map prod/confout.gro to conf.gro and scale volume

In [ ]:
def map_confout_gromacs():
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {k: fg_sys_types[k] for k in ['pyridine']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure-large']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['hncnt-hncinitlong']}
    
    # iterate md setups
    # gromacs to gromacs and gromacs to lammps
    for cg_problem_md, fg_sys_type_key, state_key, statepoints, working_dir_md in md_iterator(
        {k: v for k, v in fg_sys_types_to_do.items() if v['md-settings']['md-program'] == 'gromacs'},
        states_to_do, mappings_to_do, 
        #{k: v for k, v in cg_sys_types.items() if v['md-settings']['md-program'] == 'gromacs'},
        cg_sys_types,
        votca_settings_to_do, return_keys=True):
        
        statepoints = gen_statepoints(cg_problem_md['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            working_dir_md = os.path.abspath(os.path.join(fg_sys_type_key, state_key, 'fg', statepoint['path']))
            
            # average volume
            if statepoint['volume-cg'] == 'fg average':
                with WorkingDir(working_dir_md), tempfile.TemporaryDirectory() as tempdir:
                    run_bash(f"gmx energy -f prod/ener.edr -o {tempdir}/energy-temp.xvg <<< 'Volume'")
                    data, _ = gt.xvg.load(f"{tempdir}/energy-temp.xvg")
                volume_cg = np.mean(data['Volume'])
            elif type(statepoint['volume-cg']) in (int, float):
                volume_cg = statepoint['volume-cg']
            else:
                raise Exception('not implemented')
            
            # iterate cg problems
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
                {fg_sys_type_key: fg_sys_types[fg_sys_type_key]},
                {state_key: states[state_key]},
                mappings, cg_sys_types, votca_settings, return_keys=True, return_indices=True, print_keys=True):
                working_dir_cg = os.path.abspath(os.path.join(cg_problem['folder']))
                working_dir_cg_state = os.path.join(cg_problem['folder'], statepoint['path'])
                with WorkingDir(working_dir_cg_state), tempfile.TemporaryDirectory() as tempdir:
                    mapping_files = ';'.join(f"{working_dir_cg}/map-{moltype_key}.xml" for moltype_key in cg_problem['fg-topology']['moltypes'].keys())
                    topol_tpr = ("topol/topol-gmx-votca.tpr"
                                 if os.path.exists(f"{working_dir_md}/topol/topol-gmx-votca.tpr")
                                 else "prod/topol.tpr")
                    if cg_problem['cg-md-settings']['md-program'] == 'gromacs':
                        run_bash(f"csg_map --top {working_dir_md}/{topol_tpr} --trj {working_dir_md}/prod/confout.gro "
                                 f"--cg '{mapping_files}' --vel --out {tempdir}/conf-unscaled.gro")
                        volume_gro = np.prod(gt.gro.get_box(f"{tempdir}/conf-unscaled.gro")[0:3])
                        scale = (volume_cg / volume_gro)**(1/3)
                        # scale and make molecules whole
                        run_bash(f"gmx editconf -f {tempdir}/conf-unscaled.gro -o conf.gro -pbc -scale {scale} {scale} {scale}")
                        run_bash("rm -f \#*")
                        volume_new = np.prod(gt.gro.get_box("conf.gro")[0:3])
                        #print(volume_cg, volume_gro, volume_new)
                    elif cg_problem['cg-md-settings']['md-program'] == 'lammps':
                        run_bash(f"csg_map --top {working_dir_md}/topology.xml --trj {working_dir_md}/prod/confout.gro "
                                 f"--cg '{mapping_files}' --out {tempdir}/conf-unscaled.dump")
                        # get volume of prod-out
                        volume_gro = np.prod(gt.gro.get_box(f"{working_dir_md}/prod/confout.gro")[0:3])
                        scale = (volume_cg / volume_gro)**(1/3)
                        run_bash(fr"echo -e 'read_data lammps-unscaled.data\n"
                                 fr"read_dump {tempdir}/conf-unscaled.dump 0 x y z\n"
                                 fr"change_box all x scale {scale} y scale {scale} z scale {scale} remap\n"
                                 fr"write_data lammps.data\n"
                                 fr"write_dump all atom in.lammpstrj' | lmp -log /tmp/lammps-temp.log")
                    
map_confout_gromacs()

### generate topol.top

In [ ]:
def gen_top():
    for cg_problem in cg_setup_generator(fg_sys_types, states, mappings,
                                         {k: v for k, v in cg_sys_types.items() if v['md-settings']['md-program'] == 'gromacs'},
                                         votca_settings):
        if cg_problem['state']['type'] == 'single':
            topol = cg.gen_gromacs_topol(cg_problem, inline_moleculetypes=True)
            with WorkingDir(cg_problem['folder']):
                with open(f"topol.top", 'w') as f:
                    f.write(topol)
        elif cg_problem['state']['type'] == 'multi':
            topols = cg.gen_gromacs_topol(cg_problem, inline_moleculetypes=True)
            for i, comp_name in enumerate(cg_problem['state']['names']):
                with WorkingDir(os.path.join(cg_problem['folder'], comp_name)):
                    with open(f"topol.top", 'w') as f:
                        f.write(topols[i])
                        
gen_top()

### generate grompp.mdp

In [ ]:
def prep_mdp():
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types, states, mappings,
        {k: v for k, v in cg_sys_types.items() if v['md-settings']['md-program'] == 'gromacs'},
        votca_settings, return_keys=True, return_indices=True, print_keys=True):
        template_dir = os.path.abspath('template')
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            working_dir = os.path.abspath(os.path.join(cg_problem['folder'], statepoint['path']))
            with WorkingDir(working_dir):
                # mdp files
                run_bash(f"cp {template_dir}/mdp/cg-nvt/grompp.mdp grompp.mdp")
                gt.mdp.set_parameter("grompp.mdp", 'nsteps',
                                     int(2e6) if cg_problem['votca-settings']['inverse']['method'].lower() == 'imc'
                                     else int(2e5))
                # mdp dt, tau-t
                gt.mdp.set_parameter("grompp.mdp", 'dt', cg_problem['cg-md-settings']['dt'])
                gt.mdp.set_parameter("grompp.mdp", 'tau-t', cg_problem['cg-md-settings']['tau-t'])
                # mdp temperature
                gt.mdp.set_parameter("grompp.mdp", 'ref-t', statepoint['temperature'])
                # cut_offs
                if 'gauss_newton' in cg_problem['votca-settings']['inverse'].keys():
                    cut_off = cg_problem['votca-settings']['inverse']['gauss_newton']['cut_off']
                elif 'newton' in cg_problem['votca-settings']['inverse'].keys():
                    cut_off = cg_problem['votca-settings']['inverse']['newton']['cut_off']
                else:
                    cut_off = cg_problem['votca-settings']['non-bonded']['max']
                for key in ('rlist', 'rcoulomb', 'rvdw'):
                    gt.mdp.set_parameter("grompp.mdp", key, cut_off)
                # energygrp fields
                energygrps, energygrp_table = cg.gen_grompp_fields(cg_problem)
                gt.mdp.set_parameter("grompp.mdp", 'energygrps', energygrps)
                gt.mdp.set_parameter("grompp.mdp", 'energygrp-table', energygrp_table)
            
prep_mdp()

### generate index.ndx

In [ ]:
# needed for the pair interactions in mdp file
# temporarily create .tpr file without energytables to allow selection by atom type
def prep_ndx():
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {k: fg_sys_types[k] for k in ['pyridine']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure-large']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['mshncgnt-ibiintra-hncinit']}
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, 
        {k: v for k, v in cg_sys_types.items() if v['md-settings']['md-program'] == 'gromacs'},
        votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            working_dir = os.path.abspath(os.path.join(cg_problem['folder'], statepoint['path']))
            with WorkingDir(working_dir):
                # create topol-notables.tpr
                run_bash("cp grompp.mdp /tmp/grompp-notables.mdp")
                gt.mdp.set_parameter("/tmp/grompp-notables.mdp", 'energygrps', '')
                gt.mdp.set_parameter("/tmp/grompp-notables.mdp", 'energygrp-table', '')
                run_bash("gmx grompp -p topol.top -c conf.gro -f /tmp/grompp-notables.mdp -o /tmp/topol-notables.tpr")
                run_bash("rm -f \#* /tmp/grompp-notables.mdp")
                # commands for gmx make_ndx
                commands = 'keep 0\n'  # clear all groups except System
                commands += ''.join(list(set((fr"t {bead['type']}\n"
                                              for moltype in cg_problem['mapping']['moltypes'].values()
                                              for bead in moltype.values()))))
                commands += 'q'
                run_bash(f"echo -e '{commands}' | gmx make_ndx -f /tmp/topol-notables.tpr")
                run_bash("rm -f \#* /tmp/topol-notables.tpr")
            
prep_ndx()

### copy table.xvg

In [ ]:
def copy_table():
    for cg_problem in cg_setup_generator(fg_sys_types, states, mappings, 
                                         {k: v for k, v in cg_sys_types.items() if v['md-settings']['md-program'] == 'gromacs'},
                                         votca_settings):
        template_dir = os.path.abspath('template')
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            working_dir = os.path.abspath(os.path.join(cg_problem['folder'], statepoint['path']))
            with WorkingDir(working_dir):
                # copy table.xvg
                run_bash(f"cp {template_dir}/xvg/table.xvg table.xvg")
            
copy_table()

### generate topology.xml

(used everywhere, needed for IMC's csg_stat and IIE)

In [ ]:
def gen_xml_topol_():
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {k: fg_sys_types[k] for k in ['pyridine']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure-large']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['mshncgnt-ibiintra-hncinit']}
    
    for cg_problem in cg_setup_generator(fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do):
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            working_dir = os.path.abspath(os.path.join(cg_problem['folder'], statepoint['path']))
            with WorkingDir(working_dir):
                if cg_problem['cg-md-settings']['md-program'] == 'gromacs':
                    xml_top = cg.gen_topol_xml_cg(cg_problem, statepoint, box=gt.gro.get_box('conf.gro'))
                else:
                    box = [None, None, None]
                    with open('lammps.data', 'r') as f:
                        for line in f.readlines():
                            if 'xlo xhi' in line:
                                box[0] = (float(line.split()[1]) - float(line.split()[0])) / 10  # Å to nm
                            if 'ylo yhi' in line:
                                box[1] = (float(line.split()[1]) - float(line.split()[0])) / 10  # Å to nm
                            if 'zlo zhi' in line:
                                box[2] = (float(line.split()[1]) - float(line.split()[0])) / 10  # Å to nm
                    assert None not in box
                    xml_top = cg.gen_topol_xml_cg(cg_problem, statepoint, box=box)  # TODO volume
                xml_top.write('topology.xml')
            
gen_xml_topol_()

### generate settings.xml with correct pressure constraint

In [ ]:
def gen_settings_with_pressure_constraint():
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True, return_indices=True, print_keys=True):
        
        # not implemented for multiple statepoints
        statepoints = gen_statepoints(cg_problem['state'])
        if len(statepoints) > 1:
            print(" .. NOT IMPLEMENTED ..")
            continue
        
        try:
            p_constraint = cg_problem['votca-settings']['inverse']['gauss_newton']['pressure_constraint']
        except KeyError:
            p_constraint = None
        if (p_constraint is None or p_constraint == 'none'):
            print('no pressure correction')
            pass
        elif type(p_constraint) in (int, float):
            print('fixed value pressure correction:', p_constraint)
            pass
        elif type(p_constraint) is str:
            print(p_constraint)
            if p_constraint == "fg average minus dispersion correction":
                # average pressure and dispersion correction
                working_dir = os.path.abspath(os.path.join(cg_problem['folder'], '..', '..', 'fg'))
                with WorkingDir(working_dir), tempfile.TemporaryDirectory() as tempdir:
                    run_bash(f"gmx energy -f prod/ener.edr -o {tempdir}/energy-temp.xvg <<< 'pres.-dc'")
                    data, _ = gt.xvg.load(f"{tempdir}/energy-temp.xvg")
                    pressure_dc = np.mean(data['Pres. DC'])
                    run_bash(f"gmx energy -f prod/ener.edr -o {tempdir}/energy-temp.xvg <<< 'pressure'")
                    data, _ = gt.xvg.load(f"{tempdir}/energy-temp.xvg")
                    pressure_avg = np.mean(data['Pressure'])
                    p_constraint_val = pressure_avg + pressure_dc
                # write value to xml
                cg_problem['votca-settings']['inverse']['iie']['pressure_constraint'] = p_constraint_val
                settings_xml = cg.gen_votca_settings(cg_problem)
                with WorkingDir(cg_problem['folder']):
                    settings_xml.write(f"settings.xml")
            else:
                raise Exception("unknown pressure constraint: " + p_constraint)
        else:
            raise Exception("unknown pressure constraint: " + p_constraint)
            
gen_settings_with_pressure_constraint()

### symlink to target-dists from cg dir

In [ ]:
def link_tgt():
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['water-spce']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    # iterate all
    for cg_problem in cg_setup_generator(
        fg_sys_types_to_do, states, mappings_to_do, cg_sys_types, votca_settings,  print_keys=True,
    ):
        
        # iterate state points
        statepoints = gen_statepoints(cg_problem['state'])
        for statepoint in statepoints:
            print('   ', statepoint['path'])
            
            working_dir_cg = os.path.join(cg_problem['folder'], statepoint['path'])
            working_dir_td = os.path.abspath(os.path.join(cg_problem['tgt-dist-folder'], statepoint['path']))
            with WorkingDir(working_dir_cg):
                dir_td_rel = os.path.relpath(working_dir_td)
                for f in glob.glob(dir_td_rel + '/*.tgt'):
                    run_bash(f"rm -f {os.path.basename(f)}")
                    run_bash(f"ln -s {f} {os.path.basename(f)}")
                
link_tgt()

### copy final potentials for mixture pot.in + other initial guess

In [ ]:
def copy_pot_in():
    votca_setting_references = {
        'shncgnt0.67-hncinit': 'hncnt0.67-hncinit',
        'shncgnt0.67-avginit': 'hncnt0.67-hncinit',
        'shncgnt0.67-expinit': 'hncnt0.67-hncinit',
        'shncgnt0.67-ibiinit': 'hncnt0.67-hncinit',
        'sibi0.67-hncinit': 'hncnt0.67-hncinit',
        #'shncgn0.67-hncinit': 'hncnt0.67-hncinit',
        #'pshncgnt-hncinit': 'hncgnt0.67-hncinit',
    }
    def exp_pot(r, a, b):
        return a * np.exp(-b * r)
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['water-spce']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['x0.5']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    # iterate all
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings,  print_keys=True, return_keys=True,
    ):
        
        mol_A, mol_B = cg_problem['fg-topology']['moltypes'].keys()
        #print(mol_A, mol_B)
        
        # gen pure system paths
        # exception for ethandiol
        if fg_sys_type_key == 'ethylene_glycol' and votca_setting_key == 'pshncgnt-hncinit':
            votca_setting_reference = 'hncgnt0.67-ibiinit'
        else:
            votca_setting_reference = votca_setting_references[votca_setting_key]
        cg_problem_pure_A = cg_setup_selector(fg_sys_types, states, mappings, cg_sys_types, votca_settings, mol_A, 'pure', '1bead', votca_setting_reference, combination_settings=combination_settings)
        cg_problem_pure_B = cg_setup_selector(fg_sys_types, states, mappings, cg_sys_types, votca_settings, mol_B, 'pure', '1bead', votca_setting_reference, combination_settings=combination_settings)
        
        working_dir_cg = cg_problem['folder']
        working_dir_A = cg_problem_pure_A['folder']
        working_dir_B = cg_problem_pure_B['folder']
        
        A = working_dir_A + '/step_015/A-A.pot.cur'
        B = working_dir_B + '/step_015/A-A.pot.cur'
        run_bash(f"cp {A} {working_dir_cg}/A-A.pot.in", print_on_error=False)
        run_bash(f"cp {B} {working_dir_cg}/B-B.pot.in", print_on_error=False)
        
        if votca_setting_key.split('-')[1] == 'avginit':
            r_A, u_A, flag_A = readin_table(A)
            r_B, u_B, flag_B = readin_table(B)
            np.testing.assert_allclose(r_A, r_B)
            #np.testing.assert_allclose(flag_A, flag_B)
            # mean
            u_AB = (u_A + u_B) / 2
            # write
            writeout_table(f"{working_dir_cg}/A-B.pot.in", r_A, u_AB, flag_A)
        if votca_setting_key.split('-')[1] == 'expinit':
            # fit two exponentials to potentials and then use Good-Hope combination rule to get A-B potential guess
            r_A, u_A, flag_A = readin_table(A)
            r_B, u_B, _ = readin_table(B)
            r2_A, g_A, _ = readin_table(working_dir_cg + '/A-A.dist.tgt')
            r2_B, g_B, _ = readin_table(working_dir_cg + '/B-B.dist.tgt')
            r2_A = r2_A[0: len(r_A)]
            r2_B = r2_B[0: len(r_A)]
            g_A = g_A[0: len(r_A)]
            g_B = g_B[0: len(r_A)]
            np.testing.assert_allclose(r_A, r2_A)
            popt_A, pcov_A = optimize.curve_fit(exp_pot, r_A, u_A, sigma=1/(g_A+1e-30))
            popt_B, pcov_B = optimize.curve_fit(exp_pot, r_B, u_B, sigma=1/(g_B+1e-30))
            popt_AB = np.sqrt(popt_A * popt_B)
            u_AB = exp_pot(r_A, *popt_AB)
            # write
            writeout_table(f"{working_dir_cg}/A-B.pot.in", r_A, u_AB, flag_A)
        if votca_setting_key.split('-')[1] == 'ibiinit':
            with WorkingDir(working_dir_cg):
                run_bash("cp ../sibi0.67-hncinit/step_015/A-B.pot.cur A-B.pot.in")
            
                
copy_pot_in()

## run

### run votca

In [ ]:
# Careful: shortly deletes settings_*.xml, so running things may stop
def run_inv():
    remote_partition = 'batch'
    remote_dir_base, remote_header, remote_footer, remote_args = gen_remote_stuff(remote_host, remote_partition, ntasks=48, votca=True, exclude='node01')  #, exclude='node47,node48')
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['mix-ethyl_acetate+pyridine']}
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['mix-ethanol+tert-butanol']}
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in [key for key in fg_sys_types.keys() if 'glycol' in key]}
    
    #states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure']}
    states_to_do = {key: states[key] for key in ['x0.5']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        #'hncnt-hncinit',
        #'hncnt0.67-hncinit',
        #'hncgnt-hncinit',
        #'hncgnt0.67-hncinit',
        #'hncgnt-ibiinit',
        #'hncgnt0.67-ibiinit',
        #'shncgnt0.67-hncinit',
        #'shncgnt0.67-avginit',
        #'shncgnt0.67-expinit',
        'shncgnt0.67-ibiinit',
        #'shncgn0.67-hncinit',
        #'sibi0.67-hncinit',
    ]}
    
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        md_program = cg_problem['cg-md-settings']['md-program']
        assert md_program in ('gromacs', 'lammps')
        working_dir = os.path.join(cg_problem['folder'])
        remote_dir = os.path.join(remote_dir_base, working_dir)
        with WorkingDir(working_dir):
            # remove old settings files
            run_bash(f"ssh {remote_host} rm -f {remote_dir}/settings_*.xml")
            # push files
            filelist = ["settings*.xml", "map-cgunity-*.xml"]
            if cg_problem['votca-settings']['inverse']['initial_guess']['method'] == 'table':
                filelist += ["*.pot.in"]
            if cg_problem['votca-settings']['meta']['selected-interactions']:
                filelist += ["*.pot.in"]
            if cg_problem['state']['type'] == 'single':
                filelist += ["*.dist*.tgt"]
                if md_program == 'gromacs':
                    filelist += ["conf.gro", "grompp.mdp", "index.ndx", "table.xvg", "topol.top", "topology.xml"]
                elif md_program == 'lammps':
                    filelist += ["lammps.*", "topology.xml"]
            elif cg_problem['state']['type'] == 'multi':
                statepoints = gen_statepoints(cg_problem['state'])
                for statepoint in statepoints:
                    filelist += [statepoint['path'] + '/' + fn
                                for fn in ["conf.gro", "grompp.mdp", "index.ndx", "table.xvg", "topol.top", "topology.xml", "*.dist*.tgt"]]
            else:
                raise NotImplementedError(f"state type {cg_problem['state']['type']} not implemented")
            try:
                gt.remote.push_files(filelist, remote_host, remote_dir)
            except subprocess.CalledProcessError:
                print(".. not all needed files found, skipping this job .. ")
                continue
            # script to run
            script = remote_header + f"""
# load gromacs version of spack
spack unload gromacs
spack load $spack_gmx_for_votca

rm -f jobtmp
ln -s $JOBTMP jobtmp
# if not present votca cant continue steps, says they are in a strange state
touch jobtmp/traj.xtc
# rm done file to extend
rm -f done
""" 
            if os.path.exists('settings_step0.xml'):
                script += f"""
csg_inverse --options settings_step0.xml
rm done
""" 
            script += f"""
csg_inverse --options settings.xml
unlink jobtmp
""" 
            script += remote_footer

            jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir, dry_run=False)
            print(jobid)
            if jobid != None:
                jobids.append(jobid)
run_inv()

### check job status

In [ ]:
jobids = check_job_stati(jobids, remote_host)

### pull files from cluster

In [ ]:
def pull_cg():
    remote_dir_base, remote_header, remote_footer, remote_args = gen_remote_stuff(remote_host, 'batch', ntasks=24, votca=False)
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['pyridine']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['x0.5']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy', 'unity']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        #'hncnt-hncinit',
        #'shncgnt0.67-ibiinit',
        'sibi0.67-hncinit',
    ]}
    
    for cg_problem in cg_setup_generator(fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do):
        working_dir = os.path.join(cg_problem['folder'])
        remote_dir = os.path.join(remote_dir_base, working_dir)
        with WorkingDir(working_dir):
            filelist = []
            #if cg_problem['votca-settings']['inverse']['method'] == 'iie':
            #filelist += ["step_00{0,1}/*.npz", "dcdh.npz"]
            filelist += ["step_000/calc_u_matrix-calc_c_matrix.npz"]  # to inspect c
            filelist += ["step_000/*.pot.new" , "step_*/*.pot.cur", "step_001/*.dpot.new"]
            #if cg_problem['votca-settings']['inverse']['method'] == 'imc':
            #filelist += ["step_001/*.gmc", "step_001/*.imc", "step_001/*.idx"]
            statepoints = gen_statepoints(cg_problem['state'])
            for statepoint in statepoints:
                sp = statepoint['path']
                #print('   ', sp)
                filelist += [f"step_0??/{sp}/*.dist.new", f"step_0??/{sp}/confout.gro", f"step_0??/{sp}/ener.edr"]
                filelist += [f"step_00{{0,1}}/{sp}/*.dist*.tgt"]
                #filelist += [f"step_001/{sp}/topol.tpr"]
            exclude = "traj*"
            try:
                gt.remote.pull_files(filelist, remote_host, remote_dir, exclude=exclude)
            except subprocess.CalledProcessError:
                print('.. no data ..')
                
pull_cg()

### equilibration check

In [ ]:
def check_equi_cg():
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['ethanol']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        'hncnt-hncinit',
        #'hncnt0.67-hncinit',
    ]}
    
    for cg_problem in cg_setup_generator(fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do):
        # iterate statepoints, only one for type == 'single'
        working_dir = os.path.join(cg_problem['folder'])
        statepoints = gen_statepoints(cg_problem['state'])
        with WorkingDir(working_dir):
            fig, ax = plt.subplots()
            for statepoint in statepoints:
                sp = statepoint['path']
                print(' ', sp)
                all_temps = np.array([])
                for step in range(1, cg_problem['votca-settings']['inverse']['iterations_max'] + 1):
                    try:
                        if os.path.exists(f"step_{step:03d}/{sp}/ener.edr"):
                            run_bash(f"gmx energy -f step_{step:03d}/{sp}/ener.edr -o /tmp/energy-temp.xvg <<< 'temp'")
                            data, _ = gt.xvg.load("/tmp/energy-temp.xvg")
                            run_bash(f"rm -f /tmp/energy-temp.xvg")
                            temperature = np.asarray(data['Temperature'])
                            temperature_blocks = np.reshape(temperature[1:], (10, -1))
                            #temperature_blocks = np.pad(temperature[1:].astype(float), (0, 10 - temperature[1:].size % 10), 
                                                        #mode='constant', constant_values=np.nan).reshape(10, -1)[:, :-1]
                            temperature_block_avg = np.average(temperature_blocks, axis=1)
                            all_temps = np.append(all_temps, temperature_block_avg, axis=0)
                        else:
                            print(f".. step_{step:03d}, no data ..")
                    except:
                        raise
                ax.plot(all_temps, label=sp)
                print(np.mean(all_temps) - statepoint['temperature'])
            ax.axhline(statepoint['temperature'], linestyle=':', color='k')
            ax.legend(frameon=False)
            plt.show()

check_equi_cg()

# Analysis

## plot settings

In [ ]:
SMALL_SIZE = 8
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
mpl_rc_global = {
    'figure.dpi': 120,
    'legend.frameon': False,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'xtick.top': True,
    'ytick.right': True,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
    'text.usetex': True,  # otherwise \epsilon is same as \varepsilon. Also nice font
    'text.latex.preamble': r"\usepackage[version=4]{mhchem} \usepackage{siunitx}",
    'mathtext.fontset': 'stix',
    'font.family': 'STIXGeneral',
}

In [ ]:
def gen_color_of_molecule():
    fig, ax = plt.subplots(figsize=(2.2, 1.8), dpi=200)
    color_of_molecule = {}
    for m, molecule in enumerate(molecules.keys()):
        # get from colormap
        color = mpl.colormaps.get('turbo')((m + 0.5) / (len(molecules) + 1))
        # make darker
        lightness = np.array([0.299, 0.587, 0.114]) @ color[0:3]
        color = (*(np.array(color[0:3]) / np.sqrt(lightness) / 1.5), 1.0)
        # save
        color_of_molecule[molecule] = color
        ax.plot([0, 1], [m, m], color=color)
    plt.show()
    return color_of_molecule

color_of_molecule = gen_color_of_molecule()

In [ ]:
label_of_method = {
    # (method, target_dcdh, GN): label
    'ibi': 'IBI',
    'imc': 'IMC',
    'imcgn': 'IMCGN',
    'hncn': 'HNCN',
    'hncnt': 't-HNCN',
    'hncnt0.67': r't-HNCN$\times$0.67',
    'hncgn': 'HNCGN',
    'hncgnt': r'$p\hspace{0.07em}$-t-HNCGN',
    'hncgnt0.67': r'$p\hspace{0.07em}$-t-HNCGN$\times$0.67',
    'mshncgn': 'HNCGN',
    'mshncgn0.67': 'HNCGN',
    'mshncgnt': 't-HNCGN',
    'mshncgnt0.67': 't-HNCGN',
    'shncgnt': 's-t-HNCGN',
    'shncgnt0.67': r's-t-HNCGN$\times$0.67',
    'shncgn0.67': r's-HNCGN$\times$0.67',
}

In [ ]:
# colors = ['#228833', '#4477AA', '#66CCEE', '#AA3377', '#EE6677', '#CCBB44']
color_of_method = {
    'ibi': '#c42',
    'imc': '#bb1',
    'imcgn': '#bb1',
    'hncn': '#13a',
    'hncnt': '#78f',
    'hncnt0.67': '#3a3',
    'hncgn': '#13a',
    'hncgnt': '#9Bf',
    'hncgnt0.67': '#8a8',
    'mshncgn': '#13a',
    'mshncgn0.67': '#13a',
    'mshncgnt': '#9Bf',
    'mshncgnt0.67': '#9Bf',
    'shncgnt': '#666',
    'shncgnt0.67': '#333',
    'shncgn0.67': '#633',
    'sibi0.67': '#336',
}

linestyle_of_init = {
    'bi': '-',
    'ie': '--',
    'table': ':',
}

In [ ]:
def test_plot_settings():
        
    mpl_rc_local = {'legend.handlelength': 4.5}
    with plt.rc_context({**mpl_rc_local, **mpl_rc_global}):
        fig, ax = plt.subplots()
        line_label_dict = {}
        for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
            fg_sys_types, states, mappings, cg_sys_types, votca_settings, return_keys=True, return_indices=True, print_keys=False):
            if f != 0 or m != 0:  # only one system and mapping
                continue
            init_method = cg_problem['votca-settings']['inverse']['initial_guess']['method']
            label = label_of_method[votca_setting_key.split('-')[0]]
            color = color_of_method[votca_setting_key.split('-')[0]]
            linestyle = linestyle_of_init[init_method]
            abs_v = list(votca_settings).index(votca_setting_key)
            line, = ax.plot([0, 1], [-abs_v, -abs_v], color=color, label=label, linewidth=2, linestyle=linestyle)
            line_label_dict[(label, init_method)] = (line, label)  # first row, second column
        init_methods = uniquify((im for _, im in line_label_dict.keys()))
        label_list = uniquify((label for label, _ in line_label_dict.keys()))
        empty = mpl.patches.Rectangle((0,0), 1, 1, fill=False, edgecolor='none',
                                      visible=False)
        leg = fig.legend([tuple([(line_label_dict[(label, init_method)][0] if (label, init_method) in line_label_dict.keys() else empty) for init_method in init_methods])
                          for label in label_list], label_list, handler_map={tuple: mpl.legend_handler.HandlerTuple(ndivide=2, pad=0.5)},
                         title=r'$\text{BI}\quad\text{HNC}$')
        leg.get_title().set_position((-23, 0))
        plt.show()

test_plot_settings()

## plot target distributions

### show in tgt folder

In [ ]:
def plot_tgt(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihs'], show_intra=False):
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['octane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['xrange3']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['ibi-ibiintra-hncinit', 'mshncgnt-ibiintra-hncinit']}
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        
        # only one votca setting
        if v > 0:
            continue
        
        #working_dir = os.path.join(cg_problem['folder'])
        #with WorkingDir(working_dir):
        statepoints = gen_statepoints(cg_problem['state'])
        
        fig, axes = plt.subplots(nrows=1, ncols=len(ia_to_show), figsize=[6, 2], constrained_layout=True, squeeze=False, dpi=96)

        color_dict = collections.defaultdict(lambda: None)
        for s, statepoint in enumerate(statepoints):
            sp = statepoint['path']
            print('   ', sp)
            linestyle = ['-', '--', ':'][s]


            dir_tgt = os.path.relpath(f"{cg_problem['tgt-dist-folder']}/{sp}")

            # non-bonded
            if 'non-bonded' in ia_to_show:
                ax = axes[0][0]
                #ax.set_title('non-bonded')
                onset_min, onset_max = (np.inf, 0)
                for i, cg_beadtype_pair in enumerate(itertools.combinations_with_replacement(
                    cg.core.gen_cg_beadtypes(cg_problem['fg-topology'], cg_problem['mapping']).keys(), 2
                )):
                    ia_name = '-'.join(sorted(cg_beadtype_pair))
                    dist_tgt_file = f"{dir_tgt}/{ia_name}.dist.tgt"
                    dist_tgt_r, dist_tgt_g, dist_tgt_flag = readin_table(dist_tgt_file)
                    color = color_dict[(ia_name, None)]
                    label = ia_name if color is None else None
                    line_tgt, = ax.plot(dist_tgt_r, dist_tgt_g, label=label, color=color, linestyle=linestyle)
                    color_dict[(ia_name, None)] = line_tgt.get_color()
                    if show_intra:
                        dist_intra_tgt_file = f"{dir_tgt}/{ia_name}.dist-intra.tgt"
                        dist_intra_tgt_r, dist_intra_tgt_g, dist_intra_tgt_flag = readin_table(dist_intra_tgt_file)
                        line_intra_tgt, = ax.plot(dist_intra_tgt_r, dist_intra_tgt_g, linestyle='-', color='darkred')
                        color_dict[(ia_name, 'intra')] = line_intra_tgt.get_color()
                ax.set_xlim(0)
                ax.set_xlabel(r'$r$ in nm')
                ax.set_ylabel(r'$g$')
                ax.set_ylabel(r'$g$')
                ax.legend(frameon=False, loc='upper right', ncol=4)
            # bonds
            ia_bonded = ia_to_show.copy()
            ia_bonded.remove('non-bonded')
            for i, ia in enumerate(ia_bonded):
                ax = axes[0][i+1]
                ax.set_title(ia)
                dist_files = sorted(glob.glob(f"{dir_tgt}/{ia[:-1]}*.dist.tgt"))
                for i, dist_file in enumerate(dist_files):
                    #print(i, dist_file)
                    ia_name = dist_file.split('/')[-1].split('.')[0]
                    dist_r, dist_p, dist_flag = readin_table(dist_file)
                    label = ia_name if (ia_name, None) not in color_dict.keys() else None
                    line_tgt, = ax.plot(dist_r, dist_p, label=label)
                    color_dict[(ia_name, None)] = line_tgt.get_color()
                ax.set_ylabel(r'$p$')
                if len(dist_files) > 0:
                    ax.legend(frameon=False, loc='upper right', ncol=4)
        plt.show()
            
plot_tgt(ia_to_show=['non-bonded'])

### show in votca folder

In [ ]:
def plot_tgt_votca(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihs'], show_onset=False, show_step0tgt=False, show_step1new=False, show_intra=False):
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['octane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['xrange3']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in ['ibi-ibiintra-hncinit', 'mshncgnt-ibiintra-hncinit']}
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        
        working_dir = os.path.join(cg_problem['folder'])
        with WorkingDir(working_dir):
            statepoints = gen_statepoints(cg_problem['state'])
            for statepoint in statepoints:
                sp = statepoint['path']
                print('   ', sp)

                fig, axes = plt.subplots(nrows=1, ncols=len(ia_to_show), figsize=[6, 2], constrained_layout=True, squeeze=False, dpi=96)
            
                # non-bonded
                if 'non-bonded' in ia_to_show:
                    ax = axes[0][0]
                    #ax.set_title('non-bonded')
                    onset_min, onset_max = (np.inf, 0)
                    for i, cg_beadtype_pair in enumerate(itertools.combinations_with_replacement(
                        cg.core.gen_cg_beadtypes(cg_problem['fg-topology'], cg_problem['mapping']).keys(), 2
                    )):
                        ia_name = '-'.join(sorted(cg_beadtype_pair))
                        #print(ia_name)
                        dist_tgt_file = f"{sp}/{ia_name}.dist.tgt"
                        dist_tgt_r, dist_tgt_g, dist_tgt_flag = readin_table(dist_tgt_file)
                        line_tgt, = ax.plot(dist_tgt_r, dist_tgt_g, linestyle='-', label=ia_name)
                        if show_intra:
                            dist_intra_tgt_file = f"{sp}/{ia_name}.dist-intra.tgt"
                            dist_intra_tgt_r, dist_intra_tgt_g, dist_intra_tgt_flag = readin_table(dist_intra_tgt_file)
                            line_intra_tgt, = ax.plot(dist_intra_tgt_r, dist_intra_tgt_g, linestyle='-', color='darkred')
                        if min(np.nonzero(dist_tgt_g)[0]) < onset_min:
                            onset_min = min(np.nonzero(dist_tgt_g)[0])
                        if min(np.nonzero(dist_tgt_g)[0]) > onset_max:
                            onset_max = min(np.nonzero(dist_tgt_g)[0])
                        if show_step0tgt:
                            dist_tgt0_file = f"step_000/{sp}/{ia_name}.dist.tgt"
                            dist_tgt0_r, dist_tgt0_g, dist_tgt0_flag = readin_table(dist_tgt0_file)
                            line_tgt0, = ax.plot(dist_tgt0_r, dist_tgt0_g, linestyle='--', color=line_tgt.get_color())
                        if show_step1new:
                            dist_new1_file = f"step_001/{sp}/{ia_name}.dist.new"
                            dist_new1_r, dist_new1_g, dist_new1_flag = readin_table(dist_new1_file)
                            line_new1, = ax.plot(dist_new1_r, dist_new1_g, linestyle=':', color=line_tgt.get_color())
                    if show_onset:
                        ax.set_xlim(0.9 * dist_tgt_r[onset_min], 1.1 * dist_tgt_r[onset_max])
                        ax.set_ylim(1e-6, 1)
                        ax.set_yscale('log')
                    else:
                        ax.set_xlim(0)
                    ax.set_xlabel(r'$r$ in nm')
                    ax.set_ylabel(r'$g$')
                    ax.set_ylabel(r'$g$')
                    ax.legend(frameon=False, loc='upper right', ncol=4)
                # bonds
                ia_bonded = ia_to_show.copy()
                ia_bonded.remove('non-bonded')
                for i, ia in enumerate(ia_bonded):
                    ax = axes[0][i+1]
                    ax.set_title(ia)
                    dist_files = sorted(glob.glob(f"{sp}/{ia[:-1]}*.dist.tgt"))
                    for i, dist_file in enumerate(dist_files):
                        #print(i, dist_file)
                        ia_name = dist_file.split('/')[-1].split('.')[0]
                        dist_r, dist_p, dist_flag = readin_table(dist_file)
                        line_tgt, = ax.plot(dist_r, dist_p, label=ia_name)
                        if show_step1new:
                            dist_new1_file = f"step_001/{sp}/{ia_name}.dist.new"
                            dist_new1_r, dist_new1_g, dist_new1_flag = readin_table(dist_new1_file)
                            line_new1, = ax.plot(dist_new1_r, dist_new1_g, linestyle=':', color=line_tgt.get_color())
                    ax.set_ylabel(r'$p$')
                    if len(dist_files) > 0:
                        ax.legend(frameon=False, loc='upper right', ncol=4)
                plt.show()
            
#plot_tgt_votca(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihs'])
#plot_tgt_votca(ia_to_show=['non-bonded'], show_intra=True)
#plot_tgt_votca(ia_to_show=['non-bonded', 'bonds'], show_step1new=True)
plot_tgt_votca(ia_to_show=['non-bonded'], show_onset=True, show_step0tgt=True)
#plot_tgt_votca(ia_to_show=['non-bonded'], show_step1new=True)
#plot_tgt_votca(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihs'], show_step1new=True)

## plot initial guess

In [ ]:
def show_initial_guess(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihedrals']):
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['octane']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in ['hncnt-hncinitshort', 'hncnt-hncinit']}
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        
        fig, axes = plt.subplots(nrows=1, ncols=len(ia_to_show), figsize=[16, 3], constrained_layout=True, squeeze=False)
        
        working_dir = os.path.join(cg_problem['folder'])
        with WorkingDir(working_dir):
            # non-bonded
            if 'non-bonded' in ia_to_show:
                ax = axes[0][0]
                ax.set_title('non-bonded')
                min_pot = 0
                for i, cg_beadtype_pair in enumerate(itertools.combinations_with_replacement(
                    cg.core.gen_cg_beadtypes(cg_problem['fg-topology'], cg_problem['mapping']).keys(), 2
                )):
                    ia_name = '-'.join(sorted(cg_beadtype_pair))
                    #print(ia_name)
                    pot_file = f"step_000/{ia_name}.pot.new"
                    pot_r, pot_U, pot_flag = readin_table(pot_file)
                    line_tgt, = ax.plot(pot_r, pot_U, linestyle='-', label=ia_name)
                    if min(pot_U) < min_pot:
                        min_pot = min(pot_U)
                    cut_off = (cg_problem['votca-settings']['inverse']['gauss_newton']['cut_off']
                               if 'gauss_newton' in cg_problem['votca-settings']['inverse']
                               else cg_problem['votca-settings']['inverse']['newton']['cut_off'])
                ax.set_xlim(0, cut_off+0.1)
                #ax.set_ylim(1.05 * min_pot, -2.05 * min_pot)
                ax.set_ylim(1.05 * min_pot, 100)
                ax.axhline(0, linestyle=':', color='grey')
                #ax.set_xlabel(r'$r$ in nm')
                ax.set_ylabel(r'$U$ in kJ/mol')
                ax.legend(loc='upper right', frameon=False)
            # bonds
            for i, ia in enumerate(ia_to_show):
                ax = axes[0][i]
                ax.set_title(ia)
                pot_files = sorted(glob.glob(f"step_000/{ia[:-1]}-*.pot.new"))
                for i, pot_file in enumerate(pot_files):
                    ia_name = pot_file.split('/')[-1].split('.')[0]
                    pot_r, pot_U, pot_flag = readin_table(pot_file)
                    ax.plot(pot_r, pot_U, label=ia_name)
                    ax.set_ylim(0, 50)
                    ax.set_ylabel(r'$U$ in kJ/mol')
                    ax.legend(frameon=False)
        plt.show()

#show_initial_guess(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihedrals'])
show_initial_guess(ia_to_show=['non-bonded'])

## plot potential update

In [ ]:
def show_potential_update(ia_to_show=['non-bonded'], step=1, compare_votca_settings=False):
    step_dir = f"step_{step:03d}"
    
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['octane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['xrange3', 'Trange3', 'Trange3high']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in ['hncn-ibiintra-hncinit', 'hncnt-ibiintra-hncinit']}
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        
        if (not compare_votca_settings) or v == 0:
            fig, axes = plt.subplots(nrows=1, ncols=len(ia_to_show), figsize=[10, 2], constrained_layout=True, squeeze=False)
            color_ia_dict = {}
        
        working_dir = os.path.join(cg_problem['folder'])
        with WorkingDir(working_dir):
            # non-bonded
            if 'non-bonded' in ia_to_show:
                ax = axes[0][0]
                ax.set_title('non-bonded')
                min_pot = 0
                for i, cg_beadtype_pair in enumerate(itertools.combinations_with_replacement(
                    cg.core.gen_cg_beadtypes(cg_problem['fg-topology'], cg_problem['mapping']).keys(), 2
                )):
                    ia_name = '-'.join(sorted(cg_beadtype_pair))
                    #print(ia_name)
                    pot_file = f"{step_dir}/{ia_name}.dpot.new"
                    pot_r, pot_U, pot_flag = readin_table(pot_file)
                    linestyle = ['-', '--', '-.', ':'][v%4] if compare_votca_settings else '-'
                    label = (ia_name if v == 0 else None) if compare_votca_settings else ia_name
                    color = color_ia_dict[ia_name] if ia_name in color_ia_dict else None
                    line, = ax.plot(pot_r, pot_U, linestyle=linestyle, label=label, color=color)
                    if ia_name not in color_ia_dict:
                        color_ia_dict[ia_name] = line.get_color()
                    if min(pot_U) < min_pot:
                        min_pot = min(pot_U)
                    cut_off = (cg_problem['votca-settings']['inverse']['iie']['cut_off']
                               if 'iie' in cg_problem['votca-settings']['inverse']
                               else cg_problem['votca-settings']['non-bonded']['max'])
                ax.set_xlim(0, cut_off+0.1)
                #ax.set_ylim(1.05 * min_pot, -2.05 * min_pot)
                #ax.set_ylim(1.05 * min_pot, 3)
                ax.set_ylim(-15, 2)
                ax.axhline(0, linestyle=':', color='grey')
                #ax.set_xlabel(r'$r$ in nm')
                ax.set_ylabel(r'$\Delta U$ in kJ/mol')
                ax.legend(loc='upper right', frameon=False)
                #ax.grid()
                    
        if (not compare_votca_settings) or votca_setting_key == list(votca_settings_to_do.keys())[-1]:
            plt.show()

show_potential_update(ia_to_show=['non-bonded'], compare_votca_settings=True)

## show first step Jacobian

In [ ]:
def load_jac_ibi(cg_problem, step=1):
    """Load IBI Jacobian for all interactions."""

    def load_jacpart_ibi(g_tgt, g_k, beta):
        """Load Jacobian part for one interaction."""
        with np.errstate(invalid='ignore', divide='ignore'):
            ibi_diag = np.nan_to_num(1 / (1/beta * np.log(g_tgt/g_k) / (g_k - g_tgt)))
            ibi_jacpart = np.nan_to_num(np.diag(ibi_diag))
        return ibi_jacpart

    if cg_problem['state']['type'] == 'single':
        n_nonbonded = sum(1 for _ in cg.gen_beadtype_pairs(cg_problem))
        n_gridpoints = (cg_problem['votca-settings']['non-bonded']['max']
                      - cg_problem['votca-settings']['non-bonded']['min']) / cg_problem['votca-settings']['non-bonded']['step'] 
        n_gridpoints = int(n_gridpoints) + 1  # boundary is included in votca
        n_jac = n_nonbonded * n_gridpoints
        ibi_jac = np.zeros((n_jac, n_jac))
        for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem)):
            nb_name = '-'.join(cg_beadtype_pair)
            with WorkingDir(cg_problem['folder']):
                r, g_k, _ = readin_table(f'step_{step:03d}/{nb_name}.dist.new')
                r, g_tgt, _ = readin_table(f'{nb_name}.dist.tgt')
            beta = 1 / oconst.k_gro / cg_problem['state']['temperature']
            jac_part = load_jacpart_ibi(g_tgt, g_k, beta)
            jac_slice = slice(i*n_gridpoints, (i+1)*n_gridpoints)  # same for row and column
            ibi_jac[jac_slice, jac_slice] = jac_part
    else:
        raise Exception('not implemented')
    return ibi_jac

In [ ]:
def load_jac_imc(cg_problem, fg_sys_type_key, step=1):
    """Load IMC Jacobian for all interactions."""
    
    def gen_dudg_from_imc_matrix(A, S, indices, volume, N_n, temperature):
        first_index = list(indices.values())[0]
        r = S[first_index[0]:first_index[1], 0]
        Delta_r = r[1] - r[0]
        beta = 1 / oconst.k_gro / temperature
        #print(n, N, Delta_r, V, beta)
        dudg = np.zeros_like(A)
        with np.errstate(divide='ignore', invalid='ignore'):
            for (in1, index1), (in2, index2) in itertools.product(indices.items(), indices.items()):
                dudg[index1[0]:index1[1], index2[0]:index2[1]] = beta * 1 / (
                    (N_n)**2 / volume / 2 * 4 * np.pi *Delta_r
                ) * np.diag(1/r**2) @ A[index1[0]:index1[1], index2[0]:index2[1]]
        dudg = np.delete(dudg, [index[0] for index in indices.values()], axis=0)
        dudg = np.delete(dudg, [index[0] for index in indices.values()], axis=1)
        return dudg

    if cg_problem['state']['type'] == 'single':
        statepoint = gen_statepoints(cg_problem['state'])[0]
        n_nonbonded = len(list(cg.gen_beadtype_pairs(cg_problem)))
        n_gridpoints = (cg_problem['votca-settings']['non-bonded']['max']
                      - cg_problem['votca-settings']['non-bonded']['min']) / cg_problem['votca-settings']['non-bonded']['step'] 
        n_gridpoints = int(n_gridpoints) + 1  # boundary is included in votca
        n_jac = n_nonbonded * n_gridpoints
        step_dir = f"step_{step:03d}"
        imc_group_name = cg_problem['votca-settings']['non-bonded']['inverse']['imc']['group']
        matrix_file = os.path.join(step_dir, f"{imc_group_name}.gmc")
        index_file = os.path.join(step_dir, f"{imc_group_name}.idx")
        dist_file = os.path.join(step_dir, f"{imc_group_name}.imc")
        with WorkingDir(cg_problem['folder']):
            A = np.loadtxt(matrix_file)
            S = np.loadtxt(dist_file)
            indices = {}
            with open(index_file, 'r') as f:
                for line in f.readlines():
                    interaction, start_end = line.split()
                    start, end = map(int, start_end.split(':'))
                    start -= 1  # votca counts from 1, i count from 0
                    indices[interaction] = (start, end)
            if cg_problem['cg-sys-type']['md-settings']['md-program'] == 'gromacs':
                volume = np.prod(gt.gro.get_box("conf.gro"))
            else:
                volume = {
                    'mwater-argon-1solute-unity+mw-imc-ibiintra-hncinit': 63.334001,
                }[cg_problem['name']]
        T = statepoint['temperature']
        # TODO, N should be a list for mixtures, obtain from states
        N_n = {  # N * n
            'ethanol-water': 1000,
            'neon-argon': 1000,
            'naphtalene': 4000,
            'water-spc': 2000,
            'methanol': 2000,
            'octane': 2000,
            'mwater-argon': 2000,
        }[fg_sys_type_key]
        imc_jac = gen_dudg_from_imc_matrix(A, S, indices, volume, N_n, T)
    else:
        raise Exception('not implemented')
    return imc_jac

In [ ]:
def load_jac_iie(cg_problem, step=1, remove_redundant=True):
    """Load IMC Jacobian for all interactions."""
    if cg_problem['state']['type'] == 'single':
        step_dir = f"step_{step:03d}"
        with WorkingDir(cg_problem['folder']):
            if cg_problem['votca-settings']['inverse']['iie']['method'] == 'newton':
                data = np.load(f"{step_dir}/newton_update-calc_jacobian.npz", allow_pickle=True)
            else:
                data = np.load(f"{step_dir}/gauss_newton_update-calc_jacobian.npz", allow_pickle=True)
            _, jac_inv_mat = data['return_value']
            # number of atom types
            n_t = len(data['settings'][()]['rhos'])
            # number of interactions
            n_i = int(n_t**2)
            n_ir = (n_t * (n_t + 1)) // 2  # without equivalents, i.e. reduced
            # number of grid points in r
            n_r = len(data['input_arrays'][()]['r'])
                        
            # generate inverse jacobian as a 2D matrix
            # this is the form in which the inverse is taken
            jac_inv_mat_2D = csg.make_matrix_2D(jac_inv_mat)
            #jac_mat_2D = csg.make_matrix_2D(jac_mat)
            jac_mat_2D = np.linalg.inv(np.nan_to_num(jac_inv_mat_2D, neginf=-1e30, posinf=1e30))
            jac_mat = csg.make_matrix_4D(jac_mat_2D, n_r, n_r, n_i, n_i)
            
            # reduce (add) columns which are derivatives with respect to the same Δg, e.g. Δg_ab and Δg_ba
            jac_red = jac_mat.copy()
            identical_cols = []
            for alpha in range(n_t):
                for beta in range(n_t):
                    if beta < alpha:
                        identical_cols.append((n_t*alpha + beta, n_t*beta + alpha))
            for col1, col2 in identical_cols:
                jac_red[:, :, :, col1] += jac_red[:, :, :, col2]
                jac_red = np.delete(jac_red, [col2], axis=-1)
            # afterwards reduce (add) rows, which produce the same Δu, e.g. e.g. Δu_ab and Δu_ba, but iie thinks it adds them individually, so we have to sum!
            for col1, col2 in identical_cols:  # actually rows
                jac_red[:, :, col1, :] += jac_red[:, :, col2, :]
                jac_red = np.delete(jac_red, [col2], axis=-2)
            # make 2D
            jac_mat_2D_red = csg.make_matrix_2D(jac_red)
            
            # remove redundant rows
            #to_remove = []
            #for beta in range(n_t):
                #for alpha in range(n_t):
                    #if beta < alpha:
                        #for k in range(n_r):
                            #to_remove.append((n_t*alpha + beta)*n_r + k)
                    #else:
                        #pass
                        # remove after cut_off
                        #for k in range(n_r, n_r):
                            #to_remove.append((n_t*alpha + beta)*n_r + k)
            #jac_mat_2D_red = jac_mat_2D
            #print(to_remove)
            #jac_mat_2D_red = np.delete(jac_mat_2D, to_remove, axis=-1)
            #jac_mat_2D_red = np.delete(jac_mat_2D_red, to_remove, axis=-2)

    else:
        step_dir = f"step_{step:03d}"
        with WorkingDir(cg_problem['folder']):
            data = np.load(f"{step_dir}/multistate_gauss_newton_update-calc_multistate_jacobian.npz", allow_pickle=True)
            jac_mat = data['return_value']
            jac_mat_2D = csg.make_matrix_2D(jac_mat)
            # HACK
            jac_mat_2D_red = jac_mat_2D
    if remove_redundant:
        return jac_mat_2D_red
    else:
        return jac_mat_2D

In [ ]:
vlim_dict = collections.defaultdict(
    lambda: 2e-2, 
    naphtalene=2e-2,
    methanol=2e-2,
)

In [ ]:
def show_jacobians(difference_of_two=False):
    #fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['water-spc']}
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['mwater-argon']}
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['neon-argon']}
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['octane']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['xrange3', 'Trange3', 'Trange3high']}
    #states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['1bead']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        'imc-ibiintra-hncinit', 'hncnt-ibiintra-hncinit',
        #'hncn-ibiintra-biinit', 'hncnt-ibiintra-biinit'
        'mshncgn-ibiintra-hncinit',
    ]}
    
    jac_diff = None
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        try:
            if cg_problem['votca-settings']['inverse']['method'] == 'ibi':
                jac = load_jac_ibi(cg_problem)
                fig, ax = plt.subplots()
                ax.plot(np.diagonal(jac))
                plt.show()
            elif cg_problem['votca-settings']['inverse']['method'] in ['imc', 'iie']:
                if cg_problem['votca-settings']['inverse']['method'] == 'imc':
                    jac = load_jac_imc(cg_problem, fg_sys_type_key)
                elif cg_problem['votca-settings']['inverse']['method'] == 'iie':
                    jac = load_jac_iie(cg_problem, remove_redundant=True)
                # show whole Jacobian
                fig, ax = plt.subplots(figsize=(6, 6), dpi=150)
                mappable = ax.imshow(jac, interpolation='none', vmin=-vlim_dict[fg_sys_type_key], vmax=vlim_dict[fg_sys_type_key], cmap='RdBu_r')
                #fig.colorbar(mappable, fraction=0.04)
                ax.get_xaxis().set_ticks([])
                ax.get_yaxis().set_ticks([])
                plt.show()
                # show diagonal of Jacobian
                fig, ax = plt.subplots(figsize=(6, 1), dpi=150)
                ax.plot(np.diag(jac))
                plt.show()
                if difference_of_two:
                    if jac_diff is None:
                        jac_diff = jac
                    else:
                        jac_diff = jac_diff - jac
            else:
                print('.. not implemented ..')
                # TODO, get it from numpy dump
                continue
        except OSError:
            print('.. no data found ..')
            raise
            
        #print(jac.shape)
        #print(np.min(jac))
        #print(np.max(jac))
        #print(np.count_nonzero(jac - np.diag(np.diagonal(jac))))
        
    if difference_of_two:
        print('difference 1 - 2:')
        fig, ax = plt.subplots(figsize=(2, 6), dpi=150)
        mappable = ax.imshow(jac_diff, interpolation='none', vmin=-vlim_dict[fg_sys_type_key], vmax=vlim_dict[fg_sys_type_key], cmap='RdBu_r')
        #fig.colorbar(mappable, fraction=0.04)
        ax.get_xaxis().set_ticks([])
        ax.get_yaxis().set_ticks([])
        plt.show()
        # show diagonal of Jacobian
        fig, ax = plt.subplots(figsize=(6, 1), dpi=150)
        ax.plot(np.diag(jac_diff))
        plt.show()

show_jacobians(difference_of_two=True)

## plot RDF convergence

In [ ]:
def show_convergence(show_legend=True):
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['octane']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['x0.5']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        'shncgnt0.67-hncinit',
        'shncgnt0.67-avginit',
        #'shncgnt0.67-expinit',
        'sibi0.67-hncinit',
    ]}
    
    #ia_to_show = 'all'
    ia_to_show = ['A-B']
    
    mpl_rc_local = {'legend.handlelength': 4.0}
    with plt.rc_context({**mpl_rc_local, **mpl_rc_global}):
        
        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[4, 2.3], constrained_layout=True, dpi=300)
            line_label_dict = {}

            # iterate in group
            print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                # stuff for label, color, linestyle
                init_method = cg_problem['votca-settings']['inverse']['initial_guess']['method']
                #label = label_of_method[votca_setting_key.split('-')[0]]
                label = votca_setting_key
                color = color_of_method[votca_setting_key.split('-')[0]]
                #linestyle = linestyle_of_init[init_method]
                linestyle = ['-', '--', ':'][v]

                # iterate files
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    min_pot = 0
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem)):
                        ia_name = '-'.join(sorted(cg_beadtype_pair))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue
                        # load tgt
                        try:
                            dist_tgt_r, dist_tgt_g, _ = readin_table(f"step_001/{ia_name}.dist.tgt")
                        except:
                            print(f".. could not load {ia_name}.dist.tgt, continue ..")
                            empty = mpl.patches.Rectangle((0,0), 1, 1, fill=False, edgecolor='none', visible=False)
                            line_label_dict[(label, init_method)] = (empty, label)  # first row, second column
                            continue
                        # load new
                        dist_files = sorted(glob.glob(f"step_*/{ia_name}.dist.new"))
                        g_std = []
                        for dist_file in dist_files:
                            step = int(re.search('step_(\d+)', dist_file).group(1))
                            try:
                                dist_new_r, dist_new_g, _ = readin_table(dist_file)
                            except:
                                print(f".. could not load {dist_file} ..")
                            g_std.append((step, np.sqrt(1/max(dist_new_r) * np.trapz(x=dist_new_r, y=(dist_new_g - dist_tgt_g)**2))))
                        if len(g_std) == 0:
                            print('.. no data, skipping ..')
                        else:
                            line, = ax.plot(*zip(*g_std), label=label, color=color, linestyle=linestyle)
                            line_label_dict[(label, init_method)] = (line, label)  # first row, second column

            # after group iteration
            ax.set_xlabel('step')
            #ax.set_ylabel(r'$\sqrt{\frac{1}{r_c} \int_0^{r_c} (g - g_\mathrm{tgt})^2 dr}$')
            ax.set_ylabel(r'$\Delta g$')
            ax.set_yscale('log')
            ax.set_xlim(0, 20)
            ax.set_ylim(1e-3, 1e-0)
            ax.set_xticks([0, 5, 10, 15, 20])
            #ax.legend(loc='upper right', frameon=False)
            init_methods = uniquify((im for _, im in line_label_dict.keys()))
            label_list = uniquify((label for label, _ in line_label_dict.keys()))
            if show_legend:
                ax.legend()
            plt.show()

show_convergence(show_legend=True)

## plot potential update convergence

In [ ]:
def show_potential_update_convergence(show_legend=True):
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['octane']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    votca_settings_to_do = votca_settings
    #votca_settings_to_do = {key: votca_settings[key] for key in ['hncgnt0.67-ibiintra-hncinit']}
    
    ia_to_show = 'all'
    #ia_to_show = ['AR-MW']
    
    mpl_rc_local = {'legend.handlelength': 4.0}
    with plt.rc_context({**mpl_rc_local, **mpl_rc_global}):
        
        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[4, 2.3], constrained_layout=True, dpi=300)
            line_label_dict = {}

            # iterate in group
            print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                # stuff for label, color, linestyle
                init_method = cg_problem['votca-settings']['inverse']['initial_guess']['method']
                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_init[init_method]

                # iterate files
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    min_pot = 0
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem)):
                        ia_name = '-'.join(sorted(cg_beadtype_pair))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue
                        # load tgt
                        try:
                            dist_tgt_r, dist_tgt_g, _ = readin_table(f"step_001/{ia_name}.dist.tgt")
                        except:
                            print(f".. could not load {ia_name}.dist.tgt, continue ..")
                            empty = mpl.patches.Rectangle((0,0), 1, 1, fill=False, edgecolor='none', visible=False)
                            line_label_dict[(label, init_method)] = (empty, label)  # first row, second column
                            continue
                        # load new
                        pot_files = sorted(glob.glob(f"step_*/{ia_name}.pot.cur"))
                        pot_std = []
                        for pot_file_a, pot_file_b in zip(pot_files[:-1], pot_files[1:]):
                            step = int(re.search('step_(\d+)', pot_file_b).group(1))
                            try:
                                pot_cur_r_a, pot_cur_u_a, _ = readin_table(pot_file_a)
                                pot_cur_r_b, pot_cur_u_b, _ = readin_table(pot_file_b)
                            except:
                                print(f".. could not load {pot_file_a} or {pot_file_b} ..")
                            np.testing.assert_allclose(pot_cur_r_a, pot_cur_r_b)
                            np.testing.assert_allclose(pot_cur_r_a, dist_tgt_r)
                            pot_std.append((step, np.sqrt(1/max(pot_cur_r_a) * np.trapz(x=pot_cur_r_a, y=dist_tgt_g * (pot_cur_u_b - pot_cur_u_a)**2))))
                        if len(pot_std) == 0:
                            print('.. no data, skipping ..')
                        else:
                            line, = ax.plot(*zip(*pot_std), label=label, color=color, linestyle=linestyle)
                            line_label_dict[(label, init_method)] = (line, label)  # first row, second column

            # after group iteration
            ax.set_xlabel('step')
            ax.set_ylabel(r'$\Delta u$')
            ax.set_yscale('log')
            #ax.set_xlim(0, 20)
            ax.set_ylim(None, 4e-0)
            init_methods = uniquify((im for _, im in line_label_dict.keys()))
            label_list = uniquify((label for label, _ in line_label_dict.keys()))
            if show_legend:
                empty = mpl.patches.Rectangle((0,0), 1, 1, fill=False, edgecolor='none',
                                              visible=False)
                leg = fig.legend([tuple([(line_label_dict[(label, init_method)][0] if (label, init_method) in line_label_dict.keys() else empty) for init_method in init_methods])
                                  for label in label_list], label_list, handler_map={tuple: mpl.legend_handler.HandlerTuple(ndivide=2, pad=0.5)},
                                 title=r'$\text{BI}\quad\text{HNC}$', loc=(0.60, 0.5))
                leg.get_title().set_position((-110, 0))
            plt.show()

show_potential_update_convergence(show_legend=True)

## plot last potential

In [ ]:
def show_last_potential(show_legend=True):
    mpl_rc_local = {'legend.handlelength': 4.0}
    with plt.rc_context({**mpl_rc_local, **mpl_rc_global}):
        
        fg_sys_types_to_do = fg_sys_types
        #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['mwater-argon']}
        
        mappings_to_do = mappings
        #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
        
        #states_to_do = states
        states_to_do = {key: states[key] for key in ['x0.5']}
        
        votca_settings_to_do = votca_settings
        #votca_settings_to_do = {key: votca_settings[key] for key in ['hncnt-hncinit']}
        
        #ia_to_show = 'all'
        ia_to_show = ['A-B']

        # groupby fg, state, mapping
        for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                  lambda x: (x[1], x[2], x[3])):

            # create figure
            fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[4, 2.3], constrained_layout=True, dpi=300)

            # iterate in group
            print(fg_sys_type_key, state_key, mapping_key)
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                print(' ', votca_setting_key)

                init_method = cg_problem['votca-settings']['inverse']['initial_guess']['method']
                label = label_of_method[votca_setting_key.split('-')[0]]
                color = color_of_method[votca_setting_key.split('-')[0]]
                linestyle = linestyle_of_init[init_method]

                # plot last potential
                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    min_pot = 0
                    # iterate interactions
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem, return_dict=True)):
                        ia_name = '-'.join(sorted((key for key, value in cg_beadtype_pair)))
                        if ia_to_show != 'all' and ia_name not in ia_to_show:
                            continue

                        print(ia_name)

                        # load pot
                        pot_files = sorted(glob.glob(f"step_???/{ia_name}.pot.cur"))
                        try:
                            pot_file = pot_files[-1]  # only last one
                            step = int(re.search('step_(\d+)', pot_file).group(1)) - 1  # -1 because we use .pot.cur
                            pot_new_r, pot_new_u, _ = readin_table(pot_file)
                        except:
                            print(f".. could not load {pot_file} ..")
                            continue
                        print(step)
                        label = label_of_method[votca_setting_key.split('-')[0]]
                        line, = ax.plot(pot_new_r, pot_new_u, label=label, color=color, linestyle=linestyle)

            ax.set_xlabel(r'$r$')
            ax.set_ylabel(r'$u(r)$')
            plt.xlim(0.25, 1.25)
            #plt.ylim(-2.5, 30)
            plt.ylim(-10, 10)
            plt.show()

show_last_potential()

## show direct correlation function

In [ ]:
def show_c(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihs'], show_intra=False):
    
    #fg_sys_types_to_do = fg_sys_types
    fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['pyridine']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['pure', 'pure-large']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        #'hncnt-hncinitshort',
        'hncnt-hncinitlong',
    ]}
    
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=True):
        
        statepoints = gen_statepoints(cg_problem['state'])
        
        fig, ax = plt.subplots(figsize=[6, 2], constrained_layout=True, dpi=96)

        color_dict = collections.defaultdict(lambda: None)
        for s, statepoint in enumerate(statepoints):
            sp = statepoint['path']
            print('   ', sp)
            linestyle = ['-', '--', ':'][s]
            
            try:
                data = np.load(f"{cg_problem['folder']}/step_000/{sp}/calc_u_matrix-calc_c_matrix.npz")
                #print(data.__dict__)
                r = data['r']
                c_mat = data['return_value']
                
                for i, cg_beadtype_pair in enumerate(itertools.combinations_with_replacement(
                    cg.core.gen_cg_beadtypes(cg_problem['fg-topology'], cg_problem['mapping']).keys(), 2
                )):
                    print(cg_beadtype_pair)
                    # TODO: indexin is likely not correct
                    ax.plot(r, c_mat[:, i, i])
                
            except FileNotFoundError:
                print(".. no data ..")
            
            #ax.set_ylim(-0.1, 0.1)
            ax.set_ylim(-0.5, 0.5)
            ax.set_xlabel(r'$r$ in nm')
            ax.set_ylabel(r'$c(r)$')
            #ax.legend(frameon=False, loc='upper right', ncol=4)
        plt.show()
            
show_c(ia_to_show=['non-bonded'])

# paper plots

## plot direct correlation function

In [ ]:
#old

In [ ]:
def plot_c(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihs'], show_annotation=False):
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['2-butanol']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        #'hncnt-hncinitshort',
        'hncnt-hncinit',
    ]}
    
    mpl_rc_local = {'legend.handlelength': 4.0}
    with plt.rc_context({**mpl_rc_local, **mpl_rc_global}):
        
        fig, ax = plt.subplots(figsize=[3.2, 1.8], constrained_layout=True, dpi=300)
        
        ax.axhline(0, linestyle=':', color='k', linewidth=0.75)
        #ax.axvline(1.2, linestyle=':', color='k', linewidth=0.75)
        
        for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False):

            color = color_of_molecule[fg_sys_type_key]
            statepoints = gen_statepoints(cg_problem['state'])

            color_dict = collections.defaultdict(lambda: None)
            for s, statepoint in enumerate(statepoints):
                sp = statepoint['path']
                #print('   ', sp)
                linestyle = ['-', '--', ':'][s]

                try:
                    data = np.load(f"{cg_problem['folder']}/step_000/{sp}/calc_u_matrix-calc_c_matrix.npz")
                    #print(data.__dict__)
                    r = data['r']
                    c_mat = data['return_value']

                    ax.plot(r, c_mat[:, 0, 0], color=color)
                    
                    if show_annotation:
                        ndx = 340
                        if abs(c_mat[ndx, 0, 0]) > 0.1:
                            ax.annotate(
                                fg_sys_type_key.replace('_', ' '),
                                (r[ndx], c_mat[ndx, 0, 0]),
                                (
                                    r[ndx] - 0.5,
                                    c_mat[ndx, 0, 0] + {
                                        '1,4-dioxane': +0.05,
                                        'ethylene_glycol': +0.05,
                                        'tert-butanol': +0.1,
                                        'pyridine': 0.1,
                                    }[fg_sys_type_key]
                                ),
                                ha='right', va='center',
                                color=color,
                                arrowprops=dict(arrowstyle="-",
                                                connectionstyle="arc3",
                                                relpos=(1.0, 0.5),
                                                fc="w",
                                               ),
                            )

                except FileNotFoundError:
                    print(".. no data ..")

        #ax.set_ylim(None, 0.6)
        ax.set_ylim(-0.85, 0.5)
        ax.set_xlabel(r'$r$ in \si{\nano\meter}')
        ax.set_ylabel(r'$c(r)$')
        #ax.set_yscale('symlog')
        #ax.legend(frameon=False, loc='upper right', ncol=4)
        fig.savefig('../figures/solvents-c.pdf')
        plt.show()
            
plot_c(ia_to_show=['non-bonded'], show_annotation=True)

In [ ]:
def plot_c(ia_to_show=['non-bonded', 'bonds', 'angles', 'dihs'], show_annotation=False):
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['2-butanol']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        #'hncnt-hncinitshort',
        'hncnt-hncinit',
    ]}
    
    mpl_rc_local = {'legend.handlelength': 4.0}
    with plt.rc_context({**mpl_rc_local, **mpl_rc_global}):
        
        fig, axes = plt.subplots(figsize=[3.2, 2.8], nrows=2, sharex='col', constrained_layout=True, dpi=300)
        
        axes[0].axhline(1, linestyle=':', color='k', linewidth=0.75)
        axes[1].axhline(0, linestyle=':', color='k', linewidth=0.75)
        
        for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
            fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False):

            color = color_of_molecule[fg_sys_type_key]
            statepoints = gen_statepoints(cg_problem['state'])

            color_dict = collections.defaultdict(lambda: None)
            for s, statepoint in enumerate(statepoints):
                sp = statepoint['path']
                #print('   ', sp)
                
                # RDF g(r)
                ia_name = 'A-A'
                dist_tgt_file = f"{cg_problem['folder']}/step_000/{ia_name}.dist.tgt"
                dist_tgt_r, dist_tgt_g, dist_tgt_flag = readin_table(dist_tgt_file)
                axes[0].plot(dist_tgt_r, dist_tgt_g, label=None, color=color, linestyle='-')
                
                if show_annotation:
                    if abs(dist_tgt_g[-1] - 1) > 0.001:
                        print(fg_sys_type_key)
                        ndx = {
                            '1,4-dioxane': 242,
                            'ethylene_glycol': 242,
                            'tert-butanol': 242,
                            'pyridine': 260,
                        }[fg_sys_type_key]
                        axes[0].annotate(
                            fg_sys_type_key.replace('_', ' '),
                            (dist_tgt_r[ndx], dist_tgt_g[ndx]),
                            (
                                dist_tgt_r[ndx] + 0.3,
                                dist_tgt_g[ndx] + {
                                    '1,4-dioxane': +0.08,
                                    'ethylene_glycol': -0.1,
                                    'tert-butanol': +0.06,
                                    'pyridine': -0.06,
                                }[fg_sys_type_key]
                            ),
                            ha='left', va='center',
                            color=color,
                            arrowprops=dict(arrowstyle="-",
                                            connectionstyle="arc3",
                                            relpos=(0.0, 0.5),
                                            fc="w",
                                           ),
                        )

                # DCF c(r)
                data = np.load(f"{cg_problem['folder']}/step_000/{sp}/calc_u_matrix-calc_c_matrix.npz")
                #print(data.__dict__)
                r = data['r']
                c_mat = data['return_value']

                axes[1].plot(r, c_mat[:, 0, 0], color=color)

                if show_annotation:
                    ndx = 340
                    if abs(c_mat[ndx, 0, 0]) > 0.1:
                        axes[1].annotate(
                            fg_sys_type_key.replace('_', ' '),
                            (r[ndx], c_mat[ndx, 0, 0]),
                            (
                                r[ndx] - 0.5,
                                c_mat[ndx, 0, 0] + {
                                    '1,4-dioxane': +0.09,
                                    'ethylene_glycol': +0.05,
                                    'tert-butanol': +0.12,
                                    'pyridine': 0.1,
                                }[fg_sys_type_key]
                            ),
                            ha='right', va='center',
                            color=color,
                            arrowprops=dict(arrowstyle="-",
                                            connectionstyle="arc3",
                                            relpos=(1.0, 0.5),
                                            fc="w",
                                           ),
                        )

        axes[0].set_xlim(0, 3.3)
        axes[0].set_ylim(0.85, 1.15)
        axes[0].set_ylabel(r'$g(r)$')
        axes[1].set_ylim(-0.85, 0.58)
        axes[1].set_xlabel(r'$r$ in \si{\nano\meter}')
        axes[1].set_ylabel(r'$c(r)$')
        fig.set_constrained_layout_pads(w_pad=0.0, h_pad=0.02, hspace=0., wspace=0.)
        fig.savefig('../figures/solvents-c.pdf')
        fig.set_constrained_layout_pads(w_pad=0.0, h_pad=0.02, hspace=0., wspace=0.)
        plt.show()
            
plot_c(ia_to_show=['non-bonded'], show_annotation=True)

In [ ]:
!cp ../figures/solvents-c.pdf ~/research/output/iie-general-paper/figures/

## convergence plot

### load all pressures

In [ ]:
# load all pressures for convergence plot
def load_pressure():
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['ethanol']}
    
    states_to_do = states
    #states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
            'hncnt-hncinit',
            'hncnt0.67-hncinit',
            'hncgnt-hncinit',
            'hncgnt0.67-hncinit',
            #'imc-hncinit',
            #'imcgn-hncinit',
            'hncgnt-ibiinit',
            'hncgnt0.67-ibiinit',
    ]}
    
    pressures = {}
    for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
        fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False):
        # iterate statepoints, only one for type == 'single'
        working_dir = os.path.join(cg_problem['folder'])
        statepoints = gen_statepoints(cg_problem['state'])
        with WorkingDir(working_dir):
            for step in range(1, cg_problem['votca-settings']['inverse']['iterations_max'] + 1):
                try:
                    if not os.path.exists(f"step_{step:03d}/ener.edr"):
                        raise
                    run_bash(f"gmx energy -f step_{step:03d}/ener.edr -b 100 -o /tmp/energy-temp.xvg <<< 'pressure'", print_on_error=False)
                    data, _ = gt.xvg.load("/tmp/energy-temp.xvg")
                    run_bash(f"rm -f /tmp/energy-temp.xvg")
                    pressure_data = np.asarray(data['Pressure'])
                    # 10 blocks
                    pressure_blocks = np.reshape(pressure_data[1:], (10, -1))
                    #pressure_blocks = np.pad(pressure[1:].astype(float), (0, 10 - pressure[1:].size % 10), 
                                                #mode='constant', constant_values=np.nan).reshape(10, -1)[:, :-1]
                    pressure_block_avg = np.mean(pressure_blocks, axis=1)
                    pressure = np.mean(pressure_block_avg)
                    pressure_std = np.std(pressure_block_avg)
                    pressures[(fg_sys_type_key, state_key, mapping_key, votca_setting_key, step, 'mean')] = pressure
                    pressures[(fg_sys_type_key, state_key, mapping_key, votca_setting_key, step, 'std')] = pressure_std
                except:
                    print(f".. step_{step:03d}, no data ..")
                    pressures[(fg_sys_type_key, state_key, mapping_key, votca_setting_key, step, 'mean')] = np.nan
                    pressures[(fg_sys_type_key, state_key, mapping_key, votca_setting_key, step, 'std')] = np.nan
    return pressures

all_pressures = load_pressure()

### plot

In [ ]:
from mpl_toolkits.axes_grid1.inset_locator import inset_axes

def plot_convergence(show_pressure=False):
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['ethylene_glycol']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['pure']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do_sets = [
        {key: votca_settings[key] for key in [
            'hncnt-hncinit',
            'hncnt0.67-hncinit',
            #'imc-hncinit',
        ]},
        {key: votca_settings[key] for key in [
            'hncgnt-hncinit',
            'hncgnt0.67-hncinit',
            #'imcgn-hncinit',
            'hncgnt-ibiinit',
            'hncgnt0.67-ibiinit',
        ]},
    ]
     
    ia_to_show = 'all'
    #ia_to_show = ['AR-MW']
    
    annotation_offsets = {
        'pyridine': 14,
        '1,4-dioxane': 7,
        'tert-butanol': 9,
        'ethylene_glycol': 6,
        'acetone': -5,
        '2-butanol': -7,
        'ethanol': -10,
        'ethyl_acetate': -13,
        'diethyl_ether': -18,
    }
    
    markers = ['s', 'o']
    linestyles = ['-', ':']
    
    mpl_rc_local = {
        'legend.handlelength': 1.6,
        'legend.columnspacing': 0.8,
        'legend.handletextpad': 0.2,
    }
    with plt.rc_context({**mpl_rc_local, **mpl_rc_global}):
        
        # create figure
        fig, axes = plt.subplots(nrows=2, ncols=1, figsize=[3.2, 5.0], constrained_layout=True, dpi=300, sharex=True)
        line_label_dict = {}
        axesins = []
        
        for z, votca_settings_to_do in enumerate(votca_settings_to_do_sets):
            ax = axes[z]
            
            # inset
            if show_pressure:
                left_bottom_top_right = [(.5, .57, .95, .82), (.5, .62, .95, .87)][z]
                axins = inset_axes(ax, width="45%", height="25%",
                                   bbox_to_anchor=left_bottom_top_right,
                                   bbox_transform=ax.transAxes, loc=3)
                axesins.append(axins)
        
            # groupby fg, state, mapping
            for (fg_sys_type_key, state_key, mapping_key), group in itertools.groupby(cg_setup_generator(
                fg_sys_types_to_do, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False),
                                                                                      lambda x: (x[1], x[2], x[3])):
                # iterate in group
                #print(fg_sys_type_key, state_key, mapping_key)
                for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in group:
                    #print(' ', votca_setting_key)

                    # stuff for label, color, linestyle
                    color = color_of_molecule[fg_sys_type_key]
                    linestyle = linestyles[v % 2]
                    marker = markers[v % 2]

                    # iterate files
                    working_dir = os.path.join(cg_problem['folder'])
                    with WorkingDir(working_dir):
                        min_pot = 0
                        for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem)):
                            ia_name = '-'.join(sorted(cg_beadtype_pair))
                            if ia_to_show != 'all' and ia_name not in ia_to_show:
                                continue
                            # load tgt
                            dist_tgt_r, dist_tgt_g, _ = readin_table(f"step_001/{ia_name}.dist.tgt")
                            # load new
                            dist_files = sorted(glob.glob(f"step_*/{ia_name}.dist.new"))
                            g_std = []
                            for dist_file in dist_files:
                                step = int(re.search('step_(\d+)', dist_file).group(1))
                                dist_new_r, dist_new_g, _ = readin_table(dist_file)
                                g_std.append((step,
                                              np.sqrt(1/max(dist_new_r) * np.trapz(
                                                  x=dist_new_r, y=(dist_new_g - dist_tgt_g)**2
                                              ))
                                             ))

                            line, = ax.plot(*zip(*g_std), color=color, linestyle=linestyle, zorder=int(g_std[0][1]*1e3), marker=marker, markersize=2.5)
                            if v == 0:
                                ax.annotate(
                                    fg_sys_type_key.replace('_', ' '),
                                    (1, g_std[0][1]),
                                    (-17, annotation_offsets[fg_sys_type_key] + z * 2.8),
                                    textcoords='offset points',
                                    ha='right', va='center',
                                    color=color,
                                    arrowprops=dict(arrowstyle="-",
                                                    connectionstyle="arc3",
                                                    relpos=(1.0, 0.5),
                                                    fc="w",
                                                   ),
                                )
                            # extra annotation glycol ibiinit
                            if v == 2 and fg_sys_type_key == 'ethylene_glycol':
                                ax.annotate(
                                    'ethylene glycol\n(after $p\hspace{0.07em}$-IBI)',
                                    (1, g_std[0][1]),
                                    (-17, 0),
                                    textcoords='offset points',
                                    ha='right', va='center',
                                    color=color,
                                    arrowprops=dict(arrowstyle="-",
                                                    connectionstyle="arc3",
                                                    relpos=(1.0, 0.5),
                                                    fc="w",
                                                   ),
                                )
                    if show_pressure:
                        step_max = 15
                        steps = range(1, step_max + 1)
                        try:
                            pressures = [all_pressures[(fg_sys_type_key, state_key, mapping_key, votca_setting_key, step, 'mean')] for step in steps]
                            pressures_std = [all_pressures[(fg_sys_type_key, state_key, mapping_key, votca_setting_key, step, 'std')] for step in steps]
                            axins.plot(steps, pressures, color=color, linestyle=linestyle, marker=marker, markersize=0.5, linewidth=0.4)
                        except:
                            pass
                            
                            
            # legend
            handles = [
                ax.plot(np.nan, np.nan, linestyle=linestyles[v % 2], color='k', marker=markers[v % 2], markersize=2.5)[0]
                for v, votca_settings_key in enumerate(list(votca_settings_to_do.keys())[0:2])  # not showing ibiinit
            ]
            labels = [
                label_of_method[votca_setting_key.split('-')[0]]
                for votca_setting_key in list(votca_settings_to_do.keys())[0:2]  # not showing ibiinit
            ]
            ax.legend(handles, labels, loc='upper right', frameon=False, ncol=2)
            

        for z, ax in enumerate(axes):
            ax.set_ylabel(r'$\chi(g)$')
            ax.set_yscale('log')
            ax.yaxis.set_label_coords(*[[-0.16, 0.32], [-0.16, 0.25]][z])
        axes[-1].set_xlim(0, 15)
        axes[0].set_ylim(None, 0.30)
        axes[1].set_ylim(None, 2.3)
        axes[-1].set_xlabel('step')
        axes[-1].set_xticks([0, 5, 10, 15])
        if show_pressure:
            axesins[1].set_ylim(-2_000, 17_000)
            axesins[0].set_title(r'$p$ in \si{bar}', pad=2.8)
            axesins[1].set_title(r'$p$ in \si{bar}', pad=2.8)
            #axesins[1].set_ylim(-100, 100)
        fig.savefig('../figures/solvents-convergence.pdf')
        plt.show()

plot_convergence(show_pressure=True)

In [ ]:
!cp ../figures/solvents-convergence.pdf ~/research/output/iie-general-paper/figures/

## mixture plot

### load data

In [ ]:
def load_data_mix():
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['ethylene_glycol']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['x0.5']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        'shncgnt0.67-hncinit',
        'shncgnt0.67-avginit',
        'shncgnt0.67-ibiinit',
        #'sibi0.67-hncinit',
    ]}
    
    mix_data = {}
    lowest_g_std = {}
    
    #for m1, (mol1_name, mol1) in enumerate(dict(sorted(molecules.items())).items()):
    for m1, (mol1_name, mol1) in enumerate(molecules.items()):
        #for m2, (mol2_name, mol2) in enumerate(dict(sorted(molecules.items())).items()):
        for m2, (mol2_name, mol2) in enumerate(molecules.items()):
            if mol1_name >= mol2_name:
                continue

            mix_key = f"mix-{mol1_name}+{mol2_name}"
            fg_sys_types_mix = {mix_key: fg_sys_types_to_do[mix_key]}

            
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
                fg_sys_types_mix, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False):

                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    
                    # load convergence data
                    # load tgt
                    ia_name = 'A-B'
                    try:
                        dist_tgt_r, dist_tgt_g, _ = readin_table(f"step_001/{ia_name}.dist.tgt")
                        # load new
                        dist_files = sorted(glob.glob(f"step_*/{ia_name}.dist.new"))
                        g_std = []
                        for dist_file in dist_files:
                            step = int(re.search('step_(\d+)', dist_file).group(1))
                            dist_new_r, dist_new_g, _ = readin_table(dist_file)
                            g_std.append((step,
                                          np.sqrt(1/max(dist_new_r) * np.trapz(
                                              x=dist_new_r, y=(dist_new_g - dist_tgt_g)**2
                                          ))
                                         ))
                        mix_data[(cg_problem['name'], 'g_std')] = g_std
                        # save which one ends lowest
                        if mix_key not in lowest_g_std.keys():
                            lowest_g_std[mix_key] = (votca_setting_key, g_std[-1][1])
                        else:
                            if lowest_g_std[mix_key][1] > g_std[-1][1]:
                                lowest_g_std[mix_key] = (votca_setting_key, g_std[-1][1])
                    except:
                        mix_data[(cg_problem['name'], 'g_std')] = None
                    
    # load RDF data
    for m1, (mol1_name, mol1) in enumerate(dict(sorted(molecules.items())).items()):
        for m2, (mol2_name, mol2) in enumerate(dict(sorted(molecules.items())).items()):
            if mol1_name >= mol2_name:
                continue

            mix_key = f"mix-{mol1_name}+{mol2_name}"
            fg_sys_types_mix = {mix_key: fg_sys_types_to_do[mix_key]}
            
            votca_setting_lowest = lowest_g_std[mix_key][0]
            votca_settings_lowest = {votca_setting_lowest: votca_settings_to_do[votca_setting_lowest]}
            
            for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
                fg_sys_types_mix, states_to_do, mappings_to_do, cg_sys_types, votca_settings_lowest, return_keys=True, return_indices=True, print_keys=False):

                working_dir = os.path.join(cg_problem['folder'])
                with WorkingDir(working_dir):
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem)):
                        ia_name = '-'.join(sorted(cg_beadtype_pair))
                        # load new
                        dist_new_r, dist_new_g, _ = readin_table(f"step_015/{ia_name}.dist.new")
                        # load tgt
                        try:
                            dist_tgt_r, dist_tgt_g, _ = readin_table(f"step_001/{ia_name}.dist.tgt")
                        except:
                            dist_tgt_r, dist_tgt_g, _ = np.array(readin_table(f"{ia_name}.dist.tgt"))[:, 0:len(dist_new_r)]
                        # save
                        mix_data[(cg_problem['name'], ia_name, 'g_tgt')] = (dist_tgt_r, dist_tgt_g)
                        mix_data[(cg_problem['name'], ia_name, 'g_new')] = (dist_new_r, dist_new_g)

    return (mix_data, lowest_g_std)

mix_data, lowest_g_std = load_data_mix()

### plot

In [ ]:
from matplotlib.offsetbox import OffsetImage, AnnotationBbox
def plot_mix():
    
    fg_sys_types_to_do = fg_sys_types
    #fg_sys_types_to_do = {key: fg_sys_types[key] for key in ['ethylene_glycol']}
    
    #states_to_do = states
    states_to_do = {key: states[key] for key in ['x0.5']}
    
    mappings_to_do = mappings
    #mappings_to_do = {key: mappings[key] for key in ['4to5heavy-longco']}
    
    #votca_settings_to_do = votca_settings
    votca_settings_to_do = {key: votca_settings[key] for key in [
        'shncgnt0.67-hncinit',
        'shncgnt0.67-avginit',
        'shncgnt0.67-ibiinit',
        #'sibi0.67-hncinit',
    ]}
    
    colors_c = ['teal', 'blueviolet', 'crimson', 'orange']
    markers_c = ['s', 'o', '<', '^']
    labels_c = ['HNC', 'AVG', 'IBI', 'I']
    handles_c = {}  # fill in loop
    
    colors_g = ['lightcoral', 'gray' , 'wheat']
    colors_g_tgt = ['maroon', 'k', 'darkgoldenrod']
    zorder_g = [10, 100, 20]
    zorder_g_tgt = [15, 105, 25]
    
    mpl_rc_local = {
        'legend.handlelength': 1.8,
        #'legend.columnspacing': 0.8,
        'legend.handletextpad': 0.6,
        'legend.labelspacing': 5.0,
    }
    with plt.rc_context({**mpl_rc_local, **mpl_rc_global}):
        
        # create figure
        fig, axes = plt.subplots(nrows=9, ncols=9, figsize=[6.5, 5.9], constrained_layout=True, dpi=150, sharex=False, sharey=False)
        
        #for m1, (mol1_name, mol1) in enumerate(dict(sorted(molecules.items())).items()):
        for m1, (mol1_name, mol1) in enumerate(molecules.items()):
            #for m2, (mol2_name, mol2) in enumerate(dict(sorted(molecules.items())).items()):
            for m2, (mol2_name, mol2) in enumerate(molecules.items()):
                
                # if molecules sorted
                #if mol1_name >= mol2_name:
                    #continue
                # if molecules unsorted
                if m1 >= m2:
                    continue
                    
                ax_c = axes[m1, m2]
                ax_g = axes[m2, m1]
                color1 = color_of_molecule[mol1_name]
                color2 = color_of_molecule[mol2_name]
                
                mol1_name_sorted, mol2_name_sorted = sorted([mol1_name, mol2_name])
                mix_key = f"mix-{mol1_name_sorted}+{mol2_name_sorted}"
                fg_sys_types_mix = {mix_key: fg_sys_types_to_do[mix_key]}
                
                votca_setting_lowest = lowest_g_std[mix_key][0]
        
                for cg_problem, fg_sys_type_key, state_key, mapping_key, votca_setting_key, f, s, m, v in cg_setup_generator(
                    fg_sys_types_mix, states_to_do, mappings_to_do, cg_sys_types, votca_settings_to_do, return_keys=True, return_indices=True, print_keys=False):

                    # stuff for label, color, linestyle
                    marker_c = markers_c[v]
                    color_c = colors_c[v]

                    # convergence
                    g_std = mix_data[(cg_problem['name'], 'g_std')]
                    if g_std is None:
                        continue
                    line, = ax_c.plot(*zip(*g_std), color=color_c, linestyle='-', marker=marker_c, markersize=1.8)
                    if votca_setting_key not in handles_c.keys():
                        handles_c[votca_setting_key] = line
                    
                    # X at end of convergence
                    if votca_setting_key == votca_setting_lowest:
                        ax_c.plot(*g_std[-1], color=color_c, linestyle='none', marker='x', markersize=6, zorder=120)
                    
                    # RDFs
                    for i, cg_beadtype_pair in enumerate(cg.gen_beadtype_pairs(cg_problem)):
                        ia_name = '-'.join(sorted(cg_beadtype_pair))
                        try:
                            r, g_tgt = mix_data[(cg_problem['name'], ia_name, 'g_tgt')]
                            _, g_new = mix_data[(cg_problem['name'], ia_name, 'g_new')]
                        except:
                            continue
                        ax_g.plot(r, g_new, linestyle='-', color=colors_g[i], zorder=zorder_g[i])
                        ax_g.plot(r, g_tgt, linestyle=':', color=colors_g_tgt[i], zorder=zorder_g_tgt[i])
                        
        # plot settings
        #for m1, (mol1_name, mol1) in enumerate(dict(sorted(molecules.items())).items()):
        for m1, (mol1_name, mol1) in enumerate(molecules.items()):
            #for m2, (mol2_name, mol2) in enumerate(dict(sorted(molecules.items())).items()):
            for m2, (mol2_name, mol2) in enumerate(molecules.items()):
                
                if mol1_name == mol2_name:
                    ax = axes[m1, m2]
                    
                    # molecule picture
                    img = plt.imread(f'../figures/{mol1_name}.png')
                    zoom = [0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.04, 0.03, 0.03][m1]
                    imagebox = OffsetImage(img, zoom=zoom)
                    imagebox.image.axes = ax
                    yfrac = [0.5, 0.5, 0.5, 0.55, 0.5, 0.5, 0.5, 0.4, 0.4][m1]
                    ab = AnnotationBbox(imagebox, (0.5, yfrac), xycoords='axes fraction',
                                        bboxprops={'lw': 0})
                    ax.add_artist(ab)
                    
                    # molecule name
                    font = {'family': 'serif',
                            'color':  'k',
                            'weight': 'normal',
                            'size': 6,
                           }
                    ax.text(0.5, 0.85, mol1_name.replace('_', ' '), transform=ax.transAxes, fontdict=font, ha='center')
                    
                    #ax.set_xlim(0, max(h, w))
                    #ax.set_ylim(0, max(h, w))
                    ax.set_axis_off()
                    ax.set_zorder(-100)
                    if m1 != 0:
                        ax.arrow(0.19, 0.5, -0.1, 0.0, head_width=0.05, head_length=0.1, fc=colors_g[0], ec=colors_g[0], transform=ax.transAxes, zorder=200)
                    if m1 != 8:
                        ax.arrow(0.5, 0.19, 0.0, -0.1, head_width=0.05, head_length=0.1, fc=colors_g[2], ec=colors_g[2], transform=ax.transAxes, zorder=200)
                    
                if m1 >= m2:
                    continue
                    
                ax_c = axes[m1, m2]
                ax_g = axes[m2, m1]
                
                ax_c.set_yscale('log')
                ax_c.set_xlim(0, 17)
                ax_c.set_ylim(1.2e-3, 2e0)
                ax_c.set_xticks([1, 5, 10, 15])
                ax_g.set_xlim(0.3, 1.2)
                ax_g.set_ylim(0, 3.4)
                ax_g.set_xticks([0.5, 1.0])
                ax_g.set_yticks([1, 2, 3])
                ax_g.tick_params(labelbottom=False, labelleft=False, labeltop=False, labelright=False)    
                ax_c.tick_params(labelbottom=False, labelleft=False, labeltop=False, labelright=False)    
                #ax_c.xaxis.set_minor_locator(plt.MaxNLocator(2))
                #locmin = mpl.ticker.LogLocator(base=10.0, subs=(0.2,0.4,0.6,0.8), numticks=12)
                #ax_c.yaxis.set_minor_locator(locmin)
                #ax_c.yaxis.set_minor_formatter(mpl.ticker.NullFormatter())
                ax_c.minorticks_off()
                
        # TOP
        #axes[0, 4].tick_params(labelbottom=False, labelleft=False, labeltop=True, labelright=False)    
        for ax_c in axes[0][1:-1]:
            ax_c.tick_params(labelbottom=False, labelleft=False, labeltop=True, labelright=False)    
        # RIGHT
        for ax_c in axes[1:-1, -1]:
            ax_c.tick_params(labelbottom=False, labelleft=False, labeltop=False, labelright=True)    
        # TOP RIGHT
        axes[0, -1].tick_params(labelbottom=False, labelleft=False, labeltop=True, labelright=True)    
        # BOTTOM
        for ax_g in axes[-1, 1:-1]:
            ax_g.tick_params(labelbottom=True, labelleft=False, labeltop=False, labelright=False)    
        # LEFT
        for ax_c in axes[1:-1, 0]:
            ax_c.tick_params(labelbottom=False, labelleft=True, labeltop=False, labelright=False)    
        # BOTTOM LEST
        axes[-1, 0].tick_params(labelbottom=True, labelleft=True, labeltop=False, labelright=False)    
        
        fig.legend(handles=handles_c.values(), labels=labels_c, ncol=1, loc=(0.85, 0.71))
                
        fig.set_constrained_layout_pads(w_pad=0.0, h_pad=0.0, hspace=0., wspace=0.)
        fig.savefig('../figures/solvents-mix.pdf', dpi=450)
        # set again for preview
        fig.set_constrained_layout_pads(w_pad=0.0, h_pad=0.0, hspace=0., wspace=0.)
        plt.show()

plot_mix()

In [ ]:
!cp ../figures/solvents-mix.pdf ~/research/output/iie-general-paper/figures/